In [1]:
!unzip organized_images.zip

Archive:  organized_images.zip
   creating: organized_images/
   creating: organized_images/driver/
   creating: organized_images/driver/Address_1/
  inflating: organized_images/driver/Address_1/10.jpg  
  inflating: organized_images/driver/Address_1/1003.jpg  
  inflating: organized_images/driver/Address_1/1004.jpg  
  inflating: organized_images/driver/Address_1/1005.jpg  
  inflating: organized_images/driver/Address_1/1006.jpg  
  inflating: organized_images/driver/Address_1/1013.jpg  
  inflating: organized_images/driver/Address_1/1018.jpg  
  inflating: organized_images/driver/Address_1/102.jpg  
  inflating: organized_images/driver/Address_1/1022.jpg  
  inflating: organized_images/driver/Address_1/1023.jpg  
  inflating: organized_images/driver/Address_1/1028.jpg  
  inflating: organized_images/driver/Address_1/1029.jpg  
  inflating: organized_images/driver/Address_1/103.jpg  
  inflating: organized_images/driver/Address_1/1030.jpg  
  inflating: organized_images/driver/Address

In [2]:
ls

organized_images/  organized_images.zip  sample_data/


In [ ]:
!zip -r /content/golfDB_json_data.zip /content/golfDB_json_data

  adding: content/golfDB_json_data/ (stored 0%)
  adding: content/golfDB_json_data/iron/ (stored 0%)
  adding: content/golfDB_json_data/iron/pose_classifier_4.tflite (deflated 12%)
  adding: content/golfDB_json_data/iron/pose_classifier_8.tflite (deflated 12%)
  adding: content/golfDB_json_data/iron/pose_classification_model_8.tflite (deflated 12%)
  adding: content/golfDB_json_data/iron/combined_1_to_4.json (deflated 84%)
  adding: content/golfDB_json_data/iron/8/ (stored 0%)
  adding: content/golfDB_json_data/iron/8/5.json (deflated 83%)
  adding: content/golfDB_json_data/iron/8/7.json (deflated 84%)
  adding: content/golfDB_json_data/iron/8/6.json (deflated 84%)
  adding: content/golfDB_json_data/iron/8/7.jsonZone.Identifier (deflated 3%)
  adding: content/golfDB_json_data/iron/8/8.jsonZone.Identifier (deflated 3%)
  adding: content/golfDB_json_data/iron/8/8.json (deflated 84%)
  adding: content/golfDB_json_data/iron/8/5.jsonZone.Identifier (deflated 3%)
  adding: content/golfDB_

In [3]:
!pip install tensorflow_docs

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 182.5/182.5 kB 2.0 MB/s eta 0:00:00


In [4]:
import tensorflow as tf
import tensorflow_hub as hub
from tensorflow_docs.vis import embed
import numpy
import cv2

# Import matplotlib libraries
from matplotlib import pyplot as plt
from matplotlib.collections import LineCollection
import matplotlib.patches as patches

# Some modules to display an animation using imageio.
import imageio
from IPython.display import HTML, display

In [5]:
model_name = "movenet_lightning" #@param ["movenet_lightning", "movenet_thunder", "movenet_lightning_f16.tflite", "movenet_thunder_f16.tflite", "movenet_lightning_int8.tflite", "movenet_thunder_int8.tflite"]

if "tflite" in model_name:
  if "movenet_lightning_f16" in model_name:
    !wget -q -O model.tflite https://tfhub.dev/google/lite-model/movenet/singlepose/lightning/tflite/float16/4?lite-format=tflite
    input_size = 192
  elif "movenet_thunder_f16" in model_name:
    !wget -q -O model.tflite https://tfhub.dev/google/lite-model/movenet/singlepose/thunder/tflite/float16/4?lite-format=tflite
    input_size = 256
  elif "movenet_lightning_int8" in model_name:
    !wget -q -O model.tflite https://tfhub.dev/google/lite-model/movenet/singlepose/lightning/tflite/int8/4?lite-format=tflite
    input_size = 192
  elif "movenet_thunder_int8" in model_name:
    !wget -q -O model.tflite https://tfhub.dev/google/lite-model/movenet/singlepose/thunder/tflite/int8/4?lite-format=tflite
    input_size = 256
  else:
    raise ValueError("Unsupported model name: %s" % model_name)

  # Initialize the TFLite interpreter
  interpreter = tf.lite.Interpreter(model_path="model.tflite")
  interpreter.allocate_tensors()

  def movenet(input_image):
    """Runs detection on an input image.

    Args:
      input_image: A [1, height, width, 3] tensor represents the input image
        pixels. Note that the height/width should already be resized and match the
        expected input resolution of the model before passing into this function.

    Returns:
      A [1, 1, 17, 3] float numpy array representing the predicted keypoint
      coordinates and scores.
    """
    # TF Lite format expects tensor type of uint8.
    input_image = tf.cast(input_image, dtype=tf.uint8)
    input_details = interpreter.get_input_details()
    output_details = interpreter.get_output_details()
    interpreter.set_tensor(input_details[0]['index'], input_image.numpy())
    # Invoke inference.
    interpreter.invoke()
    # Get the model prediction.
    keypoints_with_scores = interpreter.get_tensor(output_details[0]['index'])
    return keypoints_with_scores

else:
  if "movenet_lightning" in model_name:
    module = hub.load("https://tfhub.dev/google/movenet/singlepose/lightning/4")
    input_size = 192
  elif "movenet_thunder" in model_name:
    module = hub.load("https://tfhub.dev/google/movenet/singlepose/thunder/4")
    input_size = 256
  else:
    raise ValueError("Unsupported model name: %s" % model_name)

  def movenet(input_image):
    """Runs detection on an input image.

    Args:
      input_image: A [1, height, width, 3] tensor represents the input image
        pixels. Note that the height/width should already be resized and match the
        expected input resolution of the model before passing into this function.

    Returns:
      A [1, 1, 17, 3] float numpy array representing the predicted keypoint
      coordinates and scores.
    """
    model = module.signatures['serving_default']

    # SavedModel format expects tensor type of int32.
    input_image = tf.cast(input_image, dtype=tf.int32)
    # Run model inference.
    outputs = model(input_image)
    # Output is a [1, 1, 17, 3] tensor.
    keypoints_with_scores = outputs['output_0'].numpy()
    return keypoints_with_scores

In [11]:
import csv
import json
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
import os

# Define the input size expected by the model
input_size = 192  # Example input size, adjust based on your model's requirement

# Define the folders to process
folders = ['Address_1', 'Toe-up_2', 'Mid-Backswing_3', 'Top_4', 'Mid-Downswing_5', 'Impact_6', 'Mid-Follow-Through_7', 'Finish_8']
base_folder = r"organized_images/wedge" # driver fairway hybrid iron wedge

# Function to run inference on a single image
def process_image(image_path, pose_label):
    print(f"Processing {image_path}")
    # Load and preprocess the image
    image = tf.io.read_file(image_path)
    image = tf.image.decode_jpeg(image)
    # Resize and pad the image to fit the model's expected input size
    input_image = tf.expand_dims(image, axis=0)
    input_image = tf.image.resize_with_pad(input_image, input_size, input_size)
    # Run model inference (assuming `movenet` is defined elsewhere)
    keypoints_with_scores = movenet(input_image)
    # Convert keypoints_with_scores tensor to a NumPy array and ensure type is float
    keypoints_with_scores_np = keypoints_with_scores.astype(float)

    person_data = {"Pose": pose_label, "Keypoints": []}
    for keypoint_id, keypoint in enumerate(keypoints_with_scores_np[0][0]):
        keypoint_data = {
            "Keypoint ID": keypoint_id,
            "Y": float(keypoint[0]),
            "X": float(keypoint[1]),
            "Confidence Score": float(keypoint[2])
        }
        person_data["Keypoints"].append(keypoint_data)

    # Visualize the predictions on the image (commented out for batch processing)
    # display_image = tf.expand_dims(image, axis=0)
    # display_image = tf.cast(tf.image.resize_with_pad(display_image, 1280, 1280), dtype=tf.int32)
    # output_overlay = draw_prediction_on_image(np.squeeze(display_image.numpy(), axis=0), keypoints_with_scores)
    # plt.figure(figsize=(5, 5))
    # plt.imshow(output_overlay)
    # plt.axis('off')
    # plt.show()

    return person_data

# Process each folder
for idx, folder in enumerate(folders):
    image_folder = os.path.join(base_folder, folder)
    keypoints_json_data = []
    pose_label = folder.split('_')[0]  # Use the first part of the folder name as the pose label

    nums = idx + 1

    # Get list of images from the folder
    image_paths = [os.path.join(image_folder, f) for f in os.listdir(image_folder) if f.endswith(('.jpg', '.jpeg', '.png'))]

    # Loop through each image path and process the image
    for image_path in image_paths:
        person_data = process_image(image_path, nums)
        keypoints_json_data.append(person_data)

    # Save keypoints to a JSON file for this folder

    output_file = f'json_data/wedge/{nums}.json'
    with open(output_file, 'w') as json_file:
        json.dump(keypoints_json_data, json_file, indent=4)

    print(f"Processed {len(image_paths)} images in {folder}. JSON saved to {output_file}")

print("All folders processed.")

Processing organized_images/wedge/Address_1/1255.jpg
Processing organized_images/wedge/Address_1/900.jpg
Processing organized_images/wedge/Address_1/521.jpg
Processing organized_images/wedge/Address_1/579.jpg
Processing organized_images/wedge/Address_1/1057.jpg
Processing organized_images/wedge/Address_1/364.jpg
Processing organized_images/wedge/Address_1/1256.jpg
Processing organized_images/wedge/Address_1/1257.jpg
Processing organized_images/wedge/Address_1/899.jpg
Processing organized_images/wedge/Address_1/363.jpg
Processing organized_images/wedge/Address_1/1051.jpg
Processed 11 images in Address_1. JSON saved to json_data/wedge/1.json
Processing organized_images/wedge/Toe-up_2/1255.jpg
Processing organized_images/wedge/Toe-up_2/900.jpg
Processing organized_images/wedge/Toe-up_2/521.jpg
Processing organized_images/wedge/Toe-up_2/579.jpg
Processing organized_images/wedge/Toe-up_2/364.jpg
Processing organized_images/wedge/Toe-up_2/1256.jpg
Processing organized_images/wedge/Toe-up_2/1

In [ ]:
lse = [1,2,3,4,5]
for idx, i in enumerate(lse):
    print(idx, i)

0 1
1 2
2 3
3 4
4 5


In [ ]:
!unzip golfDB_json_data.zip

Archive:  golfDB_json_data.zip
   creating: golfDB_json_data/
   creating: golfDB_json_data/driver/
   creating: golfDB_json_data/driver/.ipynb_checkpoints/
   creating: golfDB_json_data/driver/4/
  inflating: golfDB_json_data/driver/4/1.json  
golfDB_json_data/driver/4/1.jsonZone.Identifier:  mismatching "local" filename (golfDB_json_data/driver/4/1.jsonяА║Zone.Identifier),
         continuing with "central" filename version
 extracting: golfDB_json_data/driver/4/1.jsonZone.Identifier  
  inflating: golfDB_json_data/driver/4/2.json  
golfDB_json_data/driver/4/2.jsonZone.Identifier:  mismatching "local" filename (golfDB_json_data/driver/4/2.jsonяА║Zone.Identifier),
         continuing with "central" filename version
 extracting: golfDB_json_data/driver/4/2.jsonZone.Identifier  
  inflating: golfDB_json_data/driver/4/3.json  
golfDB_json_data/driver/4/3.jsonZone.Identifier:  mismatching "local" filename (golfDB_json_data/driver/4/3.jsonяА║Zone.Identifier),
         continuing with 

In [ ]:
pwd

'/content'

In [ ]:
ls

json_data/  organized_images/  organized_images.zip  sample_data/


In [ ]:
# train and test
import numpy as np
import json
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from sklearn.model_selection import train_test_split
from tensorflow.keras.layers import Dropout
from sklearn.preprocessing import StandardScaler, LabelEncoder, OneHotEncoder
from tensorflow.keras.utils import to_categorical

# Load data from JSON file
def load_data_from_json(file_path):
    with open(file_path, 'r') as file:
        data = json.load(file)
    return data

# Preprocess the data
def preprocess_data(data):
    X = []
    y = []

    for entry in data:
        print(entry)
        pose_id = entry["Pose"]
        keypoints = entry["Keypoints"]

        # Extract X and Y coordinates
        x_coords = [kp["X"] for kp in keypoints]
        y_coords = [kp["Y"] for kp in keypoints]

        # Combine X and Y into a single feature vector
        features = x_coords + y_coords  # length of features will be 34 (17x2)
        X.append(features)
        y.append(pose_id)

    return np.array(X), np.array(y)

# Example file path (replace with your actual path)
file_path = 'golfDB_json_data/driver/combined_1_to_4.json'

# Load and process your data
data = load_data_from_json(file_path)
print("data")
print(data)
X_data, y_data = preprocess_data(data)

# # Normalize the input data
# scaler = StandardScaler()
# X_data = scaler.fit_transform(X_data)

# Encode pose labels
encoder = LabelEncoder()
y_data_encoded = encoder.fit_transform(y_data)

# Convert labels to one-hot encoding
y_data_one_hot = to_categorical(y_data_encoded, num_classes=8)

# Split the data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X_data, y_data_one_hot, test_size=0.2, random_state=42)

# Build a simple neural network model
model = Sequential([
    Dense(64, activation='relu', input_shape=(34,)),  # 34 input features
    Dropout(0.1),  # Dropout with 30% rate
    Dense(32, activation='relu'),
    Dropout(0.1),  # Dropout with 30% rate
    Dense(8, activation='softmax')  # 8 output classes for 8 poses
])

# Compile the model
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model
model.fit(X_train, y_train, epochs=15, batch_size=32, validation_split=0.2)

# Evaluate the model on the test set
test_loss, test_acc = model.evaluate(X_test, y_test)
print(f"Test accuracy: {test_acc}")

# Predict a new pose
def predict_pose(model, scaler, new_data):
    new_data_scaled = scaler.transform([new_data])
    print(type(model))
    print("new_data_scaled", type(new_data_scaled),new_data_scaled)
    new_data = np.array(new_data)
    prediction = model.predict(new_data)
    predicted_pose_id = np.argmax(prediction)
    predicted_probability = np.max(prediction)
    return predicted_pose_id, predicted_probability


def normalize_pose_data(pose_data, reference_x=0.5572794732116567, reference_y=0.1998999040023779):
    normalized_data = []
    outliers = {}

    for pose_index, pose in enumerate(pose_data):
        keypoints = pose['Keypoints']
        nose_point = keypoints[0]  # 첫 번째 좌표(코)

        # 코 좌표를 기준 좌표로 이동하기 위한 오프셋 계산
        offset_x = reference_x - nose_point['X']
        offset_y = reference_y - nose_point['Y']

        pose_outliers = {'X': 0, 'Y': 0, 'dirx':0, 'diry': 0}
        has_outliers = False

        # 모든 좌표에 대해 오프셋 적용 및 이상치 확인
        for keypoint in keypoints:
            new_x = keypoint['X'] + offset_x
            new_y = keypoint['Y'] + offset_y

            if new_x < 0:
                pose_outliers['X'] += 1
                pose_outliers['dirx'] += new_x
                has_outliers = True
            if new_x > 1:
                pose_outliers['X'] += 1
                pose_outliers['dirx'] += new_x
                has_outliers = True
            if new_y < 0:
                pose_outliers['Y'] += 1
                pose_outliers['diry'] += new_y
                has_outliers = True
            if new_y > 1:
                pose_outliers['Y'] += 1
                pose_outliers['diry'] += new_y
                has_outliers = True

            keypoint['X'] = new_x
            keypoint['Y'] = new_y

        if not has_outliers:
            normalized_data.append(pose)
        else:
            outliers[pose_index] = pose_outliers

    return normalized_data, outliers

# Example input data for prediction (replace with actual data)
# new_pose_data = [
new_pose_data = [{
          "Pose": 1,
          "Keypoints": [
            {
              "Keypoint ID": 0,
              "Y": 0.1998999040023779,
              "X": 0.5572794732116567,
              "Confidence Score": 0.38429954648017883
            },
            {
              "Keypoint ID": 1,
              "Y": 0.1857140283481573,
              "X": 0.5674509760402547,
              "Confidence Score": 0.3766421675682068
            },
            {
              "Keypoint ID": 2,
              "Y": 0.18855988191528072,
              "X": 0.5435571428798543,
              "Confidence Score": 0.3990709185600281
            },
            {
              "Keypoint ID": 3,
              "Y": 0.1848350982562994,
              "X": 0.5841666516326772,
              "Confidence Score": 0.5482219457626343
            },
            {
              "Keypoint ID": 4,
              "Y": 0.19071208642883053,
              "X": 0.5350731071494924,
              "Confidence Score": 0.5129073262214661
            },
            {
              "Keypoint ID": 5,
              "Y": 0.24788459347648373,
              "X": 0.6238423046134817,
              "Confidence Score": 0.5817942023277283
            },
            {
              "Keypoint ID": 6,
              "Y": 0.2511663358108496,
              "X": 0.5107928272746908,
              "Confidence Score": 0.5316048860549927
            },
            {
              "Keypoint ID": 7,
              "Y": 0.3229065756694769,
              "X": 0.6461649593376028,
              "Confidence Score": 0.3576698303222656
            },
            {
              "Keypoint ID": 8,
              "Y": 0.32904674815101376,
              "X": 0.5030016657375204,
              "Confidence Score": 0.23619356751441956
            },
            {
              "Keypoint ID": 9,
              "Y": 0.3073511342899298,
              "X": 0.6697701868080007,
              "Confidence Score": 0.4405936896800995
            },
            {
              "Keypoint ID": 10,
              "Y": 0.391438684930036,
              "X": 0.5274413880370962,
              "Confidence Score": 0.124388687312603
            },
            {
              "Keypoint ID": 11,
              "Y": 0.4263933520214056,
              "X": 0.5869002398513662,
              "Confidence Score": 0.5152628421783447
            },
            {
              "Keypoint ID": 12,
              "Y": 0.4233699064151739,
              "X": 0.5177237745784627,
              "Confidence Score": 0.29457661509513855
            },
            {
              "Keypoint ID": 13,
              "Y": 0.5784742455379461,
              "X": 0.6054537352584707,
              "Confidence Score": 0.58955317735672
            },
            {
              "Keypoint ID": 14,
              "Y": 0.5684495191471075,
              "X": 0.4699011501335012,
              "Confidence Score": 0.333624929189682
            },
            {
              "Keypoint ID": 15,
              "Y": 0.7090776185886358,
              "X": 0.6185544785522329,
              "Confidence Score": 0.44528064131736755
            },
            {
              "Keypoint ID": 16,
              "Y": 0.691163740624616,
              "X": 0.4439542349838125,
              "Confidence Score": 0.6086346507072449
            }
          ]
        },
        {
            "Pose": 8,
            "Keypoints": [
                {
                    "Keypoint ID": 0,
                    "Y": 0.370492160320282,
                    "X": 0.564460277557373,
                    "Confidence Score": 0.2644650638103485
                },
                {
                    "Keypoint ID": 1,
                    "Y": 0.3610127866268158,
                    "X": 0.5589497685432434,
                    "Confidence Score": 0.22102594375610352
                },
                {
                    "Keypoint ID": 2,
                    "Y": 0.363131582736969,
                    "X": 0.5618407726287842,
                    "Confidence Score": 0.23655946552753448
                },
                {
                    "Keypoint ID": 3,
                    "Y": 0.358137309551239,
                    "X": 0.5450335741043091,
                    "Confidence Score": 0.31598296761512756
                },
                {
                    "Keypoint ID": 4,
                    "Y": 0.3602719008922577,
                    "X": 0.5596615076065063,
                    "Confidence Score": 0.26577290892601013
                },
                {
                    "Keypoint ID": 5,
                    "Y": 0.39237794280052185,
                    "X": 0.5796381235122681,
                    "Confidence Score": 0.26067838072776794
                },
                {
                    "Keypoint ID": 6,
                    "Y": 0.39664697647094727,
                    "X": 0.5855475068092346,
                    "Confidence Score": 0.29100555181503296
                },
                {
                    "Keypoint ID": 7,
                    "Y": 0.4401192367076874,
                    "X": 0.5971024036407471,
                    "Confidence Score": 0.23591837286949158
                },
                {
                    "Keypoint ID": 8,
                    "Y": 0.4565586745738983,
                    "X": 0.6033644676208496,
                    "Confidence Score": 0.18444178998470306
                },
                {
                    "Keypoint ID": 9,
                    "Y": 0.41204261779785156,
                    "X": 0.6138898134231567,
                    "Confidence Score": 0.08699461072683334
                },
                {
                    "Keypoint ID": 10,
                    "Y": 0.4439980387687683,
                    "X": 0.6155130863189697,
                    "Confidence Score": 0.08299459517002106
                },
                {
                    "Keypoint ID": 11,
                    "Y": 0.5488619804382324,
                    "X": 0.5801564455032349,
                    "Confidence Score": 0.32420292496681213
                },
                {
                    "Keypoint ID": 12,
                    "Y": 0.5494285225868225,
                    "X": 0.5694858431816101,
                    "Confidence Score": 0.34444400668144226
                },
                {
                    "Keypoint ID": 13,
                    "Y": 0.662931501865387,
                    "X": 0.5655375719070435,
                    "Confidence Score": 0.26281413435935974
                },
                {
                    "Keypoint ID": 14,
                    "Y": 0.6643322110176086,
                    "X": 0.5585334897041321,
                    "Confidence Score": 0.26970577239990234
                },
                {
                    "Keypoint ID": 15,
                    "Y": 0.7981950044631958,
                    "X": 0.6223082542419434,
                    "Confidence Score": 0.2421654760837555
                },
                {
                    "Keypoint ID": 16,
                    "Y": 0.7981244325637817,
                    "X": 0.6230587959289551,
                    "Confidence Score": 0.26794394850730896
                }
            ]
        }
]

result1, result2 = normalize_pose_data(new_pose_data)

# new_data = new_pose_data[0]["Keypoints"]
new_data = result1[1]["Keypoints"]
new_pose_features = [kp["X"] for kp in new_data] + [kp["Y"] for kp in new_data]
predicted_pose_id, predicted_probability = predict_pose(model, scaler, new_pose_features)
print(f"Predicted Pose ID: {predicted_pose_id}, Probability: {predicted_probability}")


# Save the model in TensorFlow format (HDF5 format)
model.save('golfDB_json_data/driver/pose_classification_model_4.h5')  # This saves the model as a .h5 file

# # Save the model in TensorFlow's SavedModel format (default)
# model.save('saved_model.tf')

# Convert to TensorFlow Lite
converter = tf.lite.TFLiteConverter.from_keras_model(model)
tflite_model = converter.convert()
with open("golfDB_json_data/driver/pose_classifier_4.tflite", "wb") as f:
    f.write(tflite_model)


# Convert the model to TensorFlow Lite
def convert_to_tflite(model_path, output_tflite_path):
    # Load the model (if it was saved in H5 format or SavedModel format)
    model = tf.keras.models.load_model(model_path)

    # Convert the model to TensorFlow Lite format
    converter = tf.lite.TFLiteConverter.from_keras_model(model)
    tflite_model = converter.convert()

    # Save the model in TensorFlow Lite format
    with open(output_tflite_path, 'wb') as f:
        f.write(tflite_model)

# Convert and save the TFLite model
convert_to_tflite('golfDB_json_data/driver/pose_classification_model_4.h5', 'golfDB_json_data/driver/pose_classification_model_4.tflite')

data
[{'Pose': 1, 'Keypoints': [{'Keypoint ID': 0, 'Y': 0.3200437128543854, 'X': 0.5245276689529419, 'Confidence Score': 0.3379109501838684}, {'Keypoint ID': 1, 'Y': 0.30446624755859375, 'X': 0.5387586355209351, 'Confidence Score': 0.4767220914363861}, {'Keypoint ID': 2, 'Y': 0.30584847927093506, 'X': 0.513020932674408, 'Confidence Score': 0.4356100261211395}, {'Keypoint ID': 3, 'Y': 0.30295583605766296, 'X': 0.5587443709373474, 'Confidence Score': 0.4334535300731659}, {'Keypoint ID': 4, 'Y': 0.3079672157764435, 'X': 0.5011427402496338, 'Confidence Score': 0.4224611520767212}, {'Keypoint ID': 5, 'Y': 0.35597896575927734, 'X': 0.6033216714859009, 'Confidence Score': 0.5528345108032227}, {'Keypoint ID': 6, 'Y': 0.37948888540267944, 'X': 0.4722220301628113, 'Confidence Score': 0.5765311121940613}, {'Keypoint ID': 7, 'Y': 0.4727003574371338, 'X': 0.608437180519104, 'Confidence Score': 0.3789849579334259}, {'Keypoint ID': 8, 'Y': 0.4899260997772217, 'X': 0.4743267297744751, 'Confidence Scor

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Epoch 1/15
27/27 ━━━━━━━━━━━━━━━━━━━━ 2s 13ms/step - accuracy: 0.2209 - loss: 1.9047 - val_accuracy: 0.2454 - val_loss: 1.5987
Epoch 2/15
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.2674 - loss: 1.5725 - val_accuracy: 0.4352 - val_loss: 1.4343
Epoch 3/15
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.2833 - loss: 1.4407 - val_accuracy: 0.2269 - val_loss: 1.4062
Epoch 4/15
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - accuracy: 0.2778 - loss: 1.4543 - val_accuracy: 0.2269 - val_loss: 1.4002
Epoch 5/15
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.2881 - loss: 1.4170 - val_accuracy: 0.2731 - val_loss: 1.3618
Epoch 6/15
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - accuracy: 0.3008 - loss: 1.3953 - val_accuracy: 0.2454 - val_loss: 1.3685
Epoch 7/15
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - accuracy: 0.2823 - loss: 1.4104 - val_accuracy: 0.4028 - val_loss: 1.3327
Epoch 8/15
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - accuracy: 0.3313 - loss: 1.3652 - val_accuracy: 0.3843 - val_loss

NameError: name 'scaler' is not defined

In [ ]:
# run this code to train
import numpy as np
import json
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical

def load_data_from_json(file_path):
    with open(file_path, 'r') as file:
        data = json.load(file)
    return data

def preprocess_data(data):
    X = []
    y = []

    for entry in data:
        pose_id = entry["Pose"]
        keypoints = entry["Keypoints"]

        # Extract X and Y coordinates
        x_coords = [kp["X"] for kp in keypoints]
        y_coords = [kp["Y"] for kp in keypoints]

        # Combine X and Y into a single feature vector
        features = x_coords + y_coords  # length of features will be 34 (17x2)
        X.append(features)
        y.append(pose_id)

    return np.array(X), np.array(y)

# Example file path (replace with your actual path)
# file_path = 'golfDB_test/total/normalized_pose_data_4.json'
file_path = 'golfDB_json_data/driver/combined_1_to_4.json'

# Load and process your data
data = load_data_from_json(file_path)
X_data, y_data = preprocess_data(data)

# Encode pose labels
encoder = LabelEncoder()
y_data_encoded = encoder.fit_transform(y_data)

# Convert labels to one-hot encoding
num_classes = len(np.unique(y_data))
y_data_one_hot = to_categorical(y_data_encoded, num_classes=num_classes)
print("num_classes",num_classes)
# Split the data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X_data, y_data_one_hot, test_size=0.2, random_state=42)

# Build a simple neural network model
model = Sequential([
    Dense(64, activation='relu', input_shape=(34,)),  # 34 input features
    Dropout(0.1),
    Dense(32, activation='relu'),
    Dropout(0.1),
    Dense(num_classes, activation='softmax')  # num_classes output classes
])

# Compile the model
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model
model.fit(X_train, y_train, epochs=25, batch_size=32, validation_split=0.2)

# Evaluate the model on the test set
test_loss, test_acc = model.evaluate(X_test, y_test)
print(f"Test accuracy: {test_acc}")

# Predict a new pose
def predict_pose(model, new_data):
    new_data = np.array([new_data])
    prediction = model.predict(new_data)
    predicted_pose_id = np.argmax(prediction)
    predicted_probability = np.max(prediction)
    return predicted_pose_id, predicted_probability

def normalize_pose_data(pose_data, reference_x=0.5572794732116567, reference_y=0.1998999040023779):
    normalized_data = []
    outliers = {}

    for pose_index, pose in enumerate(pose_data):
        keypoints = pose['Keypoints']
        nose_point = keypoints[0]  # First coordinate (nose)

        # Calculate offset to move nose coordinate to reference point
        offset_x = reference_x - nose_point['X']
        offset_y = reference_y - nose_point['Y']

        pose_outliers = {'X': 0, 'Y': 0, 'dirx':0, 'diry': 0}
        has_outliers = False

        # Apply offset to all coordinates and check for outliers
        for keypoint in keypoints:
            new_x = keypoint['X'] + offset_x
            new_y = keypoint['Y'] + offset_y

            if new_x < 0 or new_x > 1:
                pose_outliers['X'] += 1
                pose_outliers['dirx'] += new_x
                has_outliers = True
            if new_y < 0 or new_y > 1:
                pose_outliers['Y'] += 1
                pose_outliers['diry'] += new_y
                has_outliers = True

            keypoint['X'] = new_x
            keypoint['Y'] = new_y

        if not has_outliers:
            normalized_data.append(pose)
        else:
            outliers[pose_index] = pose_outliers

    return normalized_data, outliers

# Example input data for prediction (replace with actual data)
new_pose_data = [{
          "Pose": 1,
          "Keypoints": [
            {
              "Keypoint ID": 0,
              "Y": 0.1998999040023779,
              "X": 0.5572794732116567,
              "Confidence Score": 0.38429954648017883
            },
            {
              "Keypoint ID": 1,
              "Y": 0.1857140283481573,
              "X": 0.5674509760402547,
              "Confidence Score": 0.3766421675682068
            },
            {
              "Keypoint ID": 2,
              "Y": 0.18855988191528072,
              "X": 0.5435571428798543,
              "Confidence Score": 0.3990709185600281
            },
            {
              "Keypoint ID": 3,
              "Y": 0.1848350982562994,
              "X": 0.5841666516326772,
              "Confidence Score": 0.5482219457626343
            },
            {
              "Keypoint ID": 4,
              "Y": 0.19071208642883053,
              "X": 0.5350731071494924,
              "Confidence Score": 0.5129073262214661
            },
            {
              "Keypoint ID": 5,
              "Y": 0.24788459347648373,
              "X": 0.6238423046134817,
              "Confidence Score": 0.5817942023277283
            },
            {
              "Keypoint ID": 6,
              "Y": 0.2511663358108496,
              "X": 0.5107928272746908,
              "Confidence Score": 0.5316048860549927
            },
            {
              "Keypoint ID": 7,
              "Y": 0.3229065756694769,
              "X": 0.6461649593376028,
              "Confidence Score": 0.3576698303222656
            },
            {
              "Keypoint ID": 8,
              "Y": 0.32904674815101376,
              "X": 0.5030016657375204,
              "Confidence Score": 0.23619356751441956
            },
            {
              "Keypoint ID": 9,
              "Y": 0.3073511342899298,
              "X": 0.6697701868080007,
              "Confidence Score": 0.4405936896800995
            },
            {
              "Keypoint ID": 10,
              "Y": 0.391438684930036,
              "X": 0.5274413880370962,
              "Confidence Score": 0.124388687312603
            },
            {
              "Keypoint ID": 11,
              "Y": 0.4263933520214056,
              "X": 0.5869002398513662,
              "Confidence Score": 0.5152628421783447
            },
            {
              "Keypoint ID": 12,
              "Y": 0.4233699064151739,
              "X": 0.5177237745784627,
              "Confidence Score": 0.29457661509513855
            },
            {
              "Keypoint ID": 13,
              "Y": 0.5784742455379461,
              "X": 0.6054537352584707,
              "Confidence Score": 0.58955317735672
            },
            {
              "Keypoint ID": 14,
              "Y": 0.5684495191471075,
              "X": 0.4699011501335012,
              "Confidence Score": 0.333624929189682
            },
            {
              "Keypoint ID": 15,
              "Y": 0.7090776185886358,
              "X": 0.6185544785522329,
              "Confidence Score": 0.44528064131736755
            },
            {
              "Keypoint ID": 16,
              "Y": 0.691163740624616,
              "X": 0.4439542349838125,
              "Confidence Score": 0.6086346507072449
            }
          ]
        },
         {
          "Pose": 2,
          "Keypoints": [
            {
              "Keypoint ID": 0,
              "Y": 0.1998999040023779,
              "X": 0.5572794732116567,
              "Confidence Score": 0.28372180461883545
            },
            {
              "Keypoint ID": 1,
              "Y": 0.19283156799239864,
              "X": 0.5516909715198385,
              "Confidence Score": 0.251054048538208
            },
            {
              "Keypoint ID": 2,
              "Y": 0.19400509404105892,
              "X": 0.5688723978065359,
              "Confidence Score": 0.20210325717926025
            },
            {
              "Keypoint ID": 3,
              "Y": 0.18713878797454586,
              "X": 0.5563201066516744,
              "Confidence Score": 0.4916621148586273
            },
            {
              "Keypoint ID": 4,
              "Y": 0.1869665007488226,
              "X": 0.5949060079120504,
              "Confidence Score": 0.45228540897369385
            },
            {
              "Keypoint ID": 5,
              "Y": 0.22883694576186886,
              "X": 0.5502192136310445,
              "Confidence Score": 0.46836769580841064
            },
            {
              "Keypoint ID": 6,
              "Y": 0.22359960483474484,
              "X": 0.6151763853095876,
              "Confidence Score": 0.5013452172279358
            },
            {
              "Keypoint ID": 7,
              "Y": 0.3095289389984106,
              "X": 0.5179182943366872,
              "Confidence Score": 0.42813655734062195
            },
            {
              "Keypoint ID": 8,
              "Y": 0.2953772466079687,
              "X": 0.6203050073646413,
              "Confidence Score": 0.3206494152545929
            },
            {
              "Keypoint ID": 9,
              "Y": 0.3581000487701391,
              "X": 0.5069270190261709,
              "Confidence Score": 0.4132034182548523
            },
            {
              "Keypoint ID": 10,
              "Y": 0.344024054278562,
              "X": 0.5395278390907156,
              "Confidence Score": 0.29419827461242676
            },
            {
              "Keypoint ID": 11,
              "Y": 0.35305248903197994,
              "X": 0.5664144214652883,
              "Confidence Score": 0.5243645906448364
            },
            {
              "Keypoint ID": 12,
              "Y": 0.3505733530418371,
              "X": 0.6199239548705923,
              "Confidence Score": 0.5773006081581116
            },
            {
              "Keypoint ID": 13,
              "Y": 0.4603362004653906,
              "X": 0.5355464574359762,
              "Confidence Score": 0.5046972036361694
            },
            {
              "Keypoint ID": 14,
              "Y": 0.46579509185714474,
              "X": 0.6434544977210866,
              "Confidence Score": 0.5903673768043518
            },
            {
              "Keypoint ID": 15,
              "Y": 0.5729835550682043,
              "X": 0.5185484048389303,
              "Confidence Score": 0.6058805584907532
            },
            {
              "Keypoint ID": 16,
              "Y": 0.5775273959533667,
              "X": 0.6776927169822561,
              "Confidence Score": 0.5113898515701294
            }
          ]
        },
          {
   "Pose": 2,
   "Keypoints": [
             {
               "Keypoint ID": 0,
               "Y": 0.1998999040023779,
               "X": 0.5572794732116567,
               "Confidence Score": 0.18655680119991302
             },
             {
               "Keypoint ID": 1,
               "Y": 0.18478064941329708,
               "X": 0.5567325111888753,
               "Confidence Score": 0.16369657218456268
             },
             {
               "Keypoint ID": 2,
               "Y": 0.193505517710874,
               "X": 0.5570587870143758,
               "Confidence Score": 0.12436198443174362
             },
             {
               "Keypoint ID": 3,
               "Y": 0.1916620652572607,
               "X": 0.5737201627754079,
               "Confidence Score": 0.16603250801563263
             },
             {
               "Keypoint ID": 4,
               "Y": 0.19272985266608944,
               "X": 0.5685089584850179,
               "Confidence Score": 0.12152981013059616
             },
             {
               "Keypoint ID": 5,
               "Y": 0.23885490702552548,
               "X": 0.5913252290748464,
               "Confidence Score": 0.201650470495224
             },
             {
               "Keypoint ID": 6,
               "Y": 0.237171791066358,
               "X": 0.5663241800330984,
               "Confidence Score": 0.20409967005252838
             },
             {
               "Keypoint ID": 7,
               "Y": 0.2890136461154913,
               "X": 0.5921955760978567,
               "Confidence Score": 0.1201537474989891
             },
             {
               "Keypoint ID": 8,
               "Y": 0.28425227807922115,
               "X": 0.5303763803504812,
               "Confidence Score": 0.22033177316188812
             },
             {
               "Keypoint ID": 9,
               "Y": 0.3697345178024267,
               "X": 0.589822536375414,
               "Confidence Score": 0.08296327292919159
             },
             {
               "Keypoint ID": 10,
               "Y": 0.2914862553970312,
               "X": 0.52138197984923,
               "Confidence Score": 0.16009913384914398
             },
             {
               "Keypoint ID": 11,
               "Y": 0.3671037475959753,
               "X": 0.6054006275199758,
               "Confidence Score": 0.23828662931919098
             },
             {
               "Keypoint ID": 12,
               "Y": 0.366550258864591,
               "X": 0.5604556855224477,
               "Confidence Score": 0.28221383690834045
             },
             {
               "Keypoint ID": 13,
               "Y": 0.48618733095092526,
               "X": 0.6517440732978689,
               "Confidence Score": 0.28772029280662537
             },
             {
               "Keypoint ID": 14,
               "Y": 0.4802650730506872,
               "X": 0.5336893257163869,
               "Confidence Score": 0.3861292600631714
             },
             {
               "Keypoint ID": 15,
               "Y": 0.5927140037910437,
               "X": 0.6839636620544302,
               "Confidence Score": 0.3717656135559082
             },
             {
               "Keypoint ID": 16,
               "Y": 0.5978851239578222,
               "X": 0.5213201102279531,
               "Confidence Score": 0.5491869449615479
             }
           ]
         },
        {
        "Pose": 3,
        "Keypoints": [
          {
               "Keypoint ID": 0,
               "Y": 0.1998999040023779,
               "X": 0.5572794732116567,
               "Confidence Score": 0.5233508944511414
             },
             {
               "Keypoint ID": 1,
               "Y": 0.19005422996444454,
               "X": 0.5670533534549581,
               "Confidence Score": 0.41108906269073486
             },
             {
               "Keypoint ID": 2,
               "Y": 0.19183265375060787,
               "X": 0.5488169547580587,
               "Confidence Score": 0.41785308718681335
             },
             {
               "Keypoint ID": 3,
               "Y": 0.1872251551048254,
               "X": 0.5829964038394796,
               "Confidence Score": 0.359442800283432
             },
             {
               "Keypoint ID": 4,
               "Y": 0.18872528480453243,
               "X": 0.5425327178500997,
               "Confidence Score": 0.3397250175476074
             },
             {
               "Keypoint ID": 5,
               "Y": 0.22597106503410092,
               "X": 0.5999031421207296,
               "Confidence Score": 0.36322763562202454
             },
             {
               "Keypoint ID": 6,
               "Y": 0.22566648529929867,
               "X": 0.5411074515842306,
               "Confidence Score": 0.5271771550178528
             },
             {
               "Keypoint ID": 7,
               "Y": 0.27333658145828,
               "X": 0.5597523805164205,
               "Confidence Score": 0.33303192257881165
             },
             {
               "Keypoint ID": 8,
               "Y": 0.2595299999610876,
               "X": 0.4938227888606893,
               "Confidence Score": 0.3716002404689789
             },
             {
               "Keypoint ID": 9,
               "Y": 0.2674013893501257,
               "X": 0.4826879855655538,
               "Confidence Score": 0.22656208276748657
             },
             {
               "Keypoint ID": 10,
               "Y": 0.2588499109642004,
               "X": 0.4175957795642721,
               "Confidence Score": 0.3326752185821533
             },
             {
               "Keypoint ID": 11,
               "Y": 0.3651062767402624,
               "X": 0.6247091647647726,
               "Confidence Score": 0.6366832256317139
             },
             {
               "Keypoint ID": 12,
               "Y": 0.36474507259292355,
               "X": 0.5685849544071065,
               "Confidence Score": 0.6100196838378906
             },
             {
               "Keypoint ID": 13,
               "Y": 0.4840913932220434,
               "X": 0.6307024117969381,
               "Confidence Score": 0.5793138146400452
             },
             {
               "Keypoint ID": 14,
               "Y": 0.47386037515563717,
               "X": 0.5469901320003377,
               "Confidence Score": 0.4684992730617523
             },
             {
               "Keypoint ID": 15,
               "Y": 0.6038166205780005,
               "X": 0.6602253076099264,
               "Confidence Score": 0.614835798740387
             },
             {
               "Keypoint ID": 16,
               "Y": 0.6002893965141272,
               "X": 0.5348793026470052,
               "Confidence Score": 0.6604465842247009
             }
        ]
      },
     {
      "Pose": 4,
      "Keypoints": [
        {
          "Keypoint ID": 0,
          "Y": 0.1998999040023779,
          "X": 0.5572794732116567,
          "Confidence Score": 0.3467405438423157
        },
        {
          "Keypoint ID": 1,
          "Y": 0.19532193945808163,
          "X": 0.5606731232665884,
          "Confidence Score": 0.3797306716442108
        },
        {
          "Keypoint ID": 2,
          "Y": 0.19583689378661862,
          "X": 0.551107412245165,
          "Confidence Score": 0.3314727246761322
        },
        {
          "Keypoint ID": 3,
          "Y": 0.19690873431129208,
          "X": 0.577030902769457,
          "Confidence Score": 0.45247089862823486
        },
        {
          "Keypoint ID": 4,
          "Y": 0.19540642904205074,
          "X": 0.5503422376178609,
          "Confidence Score": 0.2488090842962265
        },
        {
          "Keypoint ID": 5,
          "Y": 0.23554625319404354,
          "X": 0.597602671053301,
          "Confidence Score": 0.4830474555492401
        },
        {
          "Keypoint ID": 6,
          "Y": 0.2300909976856207,
          "X": 0.5393918808959829,
          "Confidence Score": 0.4640575051307678
        },
        {
          "Keypoint ID": 7,
          "Y": 0.2597375433341955,
          "X": 0.5990965422653066,
          "Confidence Score": 0.23661795258522034
        },
        {
          "Keypoint ID": 8,
          "Y": 0.22349279331130734,
          "X": 0.4972584303878652,
          "Confidence Score": 0.2514112591743469
        },
        {
          "Keypoint ID": 9,
          "Y": 0.18169014858169308,
          "X": 0.4865576383136617,
          "Confidence Score": 0.48414140939712524
        },
        {
          "Keypoint ID": 10,
          "Y": 0.18301441477699032,
          "X": 0.4750656243823873,
          "Confidence Score": 0.3429151177406311
        },
        {
          "Keypoint ID": 11,
          "Y": 0.3608725588218664,
          "X": 0.6029389556907522,
          "Confidence Score": 0.5062991380691528
        },
        {
          "Keypoint ID": 12,
          "Y": 0.36061065601272335,
          "X": 0.5471519288085805,
          "Confidence Score": 0.5095577239990234
        },
        {
          "Keypoint ID": 13,
          "Y": 0.45916622089309445,
          "X": 0.6069391426109182,
          "Confidence Score": 0.45024603605270386
        },
        {
          "Keypoint ID": 14,
          "Y": 0.45999669240874996,
          "X": 0.542729144956957,
          "Confidence Score": 0.3652518093585968
        },
        {
          "Keypoint ID": 15,
          "Y": 0.5711054127113318,
          "X": 0.641198759939562,
          "Confidence Score": 0.5267818570137024
        },
        {
          "Keypoint ID": 16,
          "Y": 0.5709175388709997,
          "X": 0.5230086502097951,
          "Confidence Score": 0.40136680006980896
        }
      ]
    }
]

result1, result2 = normalize_pose_data(new_pose_data)
for k in range(len(new_pose_data)):
    new_data = result1[k]["Keypoints"]  # Using the first normalized pose
    new_pose_features = [kp["X"] for kp in new_data] + [kp["Y"] for kp in new_data]
    predicted_pose_id, predicted_probability = predict_pose(model, new_pose_features)
    print(f"Predicted Pose ID: {predicted_pose_id}, Probability: {predicted_probability}")

# Save the model in TensorFlow format (HDF5 format)
model.save('golfDB_json_data/driver/pose_classification_model_4.h5')

# Convert to TensorFlow Lite
converter = tf.lite.TFLiteConverter.from_keras_model(model)
tflite_model = converter.convert()
with open("golfDB_json_data/driver/pose_classifier_4.tflite", "wb") as f:
    f.write(tflite_model)

# Function to convert saved model to TFLite
def convert_to_tflite(model_path, output_tflite_path):
    model = tf.keras.models.load_model(model_path)
    converter = tf.lite.TFLiteConverter.from_keras_model(model)
    tflite_model = converter.convert()
    with open(output_tflite_path, 'wb') as f:
        f.write(tflite_model)

# Convert and save the TFLite model
convert_to_tflite('golfDB_json_data/driver/pose_classification_model_4.h5', 'golfDB_json_data/driver/pose_classification_model_4.tflite')

num_classes 4
Epoch 1/25


/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


27/27 ━━━━━━━━━━━━━━━━━━━━ 2s 15ms/step - accuracy: 0.2841 - loss: 1.3876 - val_accuracy: 0.4537 - val_loss: 1.3667
Epoch 2/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.3626 - loss: 1.3635 - val_accuracy: 0.5509 - val_loss: 1.3427
Epoch 3/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.3800 - loss: 1.3456 - val_accuracy: 0.4537 - val_loss: 1.3185
Epoch 4/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.4795 - loss: 1.3034 - val_accuracy: 0.6065 - val_loss: 1.2791
Epoch 5/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.4998 - loss: 1.2665 - val_accuracy: 0.5926 - val_loss: 1.2298
Epoch 6/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.5588 - loss: 1.2170 - val_accuracy: 0.5556 - val_loss: 1.1824
Epoch 7/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.5804 - loss: 1.1561 - val_accuracy: 0.5046 - val_loss: 1.1643
Epoch 8/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.5592 - loss: 1.0992 - val_accuracy: 0.6250 - val_loss: 1.0672
Ep

Predicted Pose ID: 3, Probability: 0.907926082611084
Saved artifact at '/tmp/tmp9mb85eyr'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='keras_tensor_6')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  132313524166624: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313524170320: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313524176320: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313524180720: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313524179312: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313524182656: TensorSpec(shape=(), dtype=tf.resource, name=None)


Saved artifact at '/tmp/tmpt550fdzh'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='input_layer_1')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  132313610868464: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313616926320: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313617123808: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313617126624: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313617129792: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313617135776: TensorSpec(shape=(), dtype=tf.resource, name=None)


In [ ]:
# run this code to train
import numpy as np
import json
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical

def load_data_from_json(file_path):
    with open(file_path, 'r') as file:
        data = json.load(file)
    return data

def preprocess_data(data):
    X = []
    y = []

    for entry in data:
        pose_id = entry["Pose"]
        keypoints = entry["Keypoints"]

        # Extract X and Y coordinates
        x_coords = [kp["X"] for kp in keypoints]
        y_coords = [kp["Y"] for kp in keypoints]

        # Combine X and Y into a single feature vector
        features = x_coords + y_coords  # length of features will be 34 (17x2)
        X.append(features)
        y.append(pose_id)

    return np.array(X), np.array(y)

# Example file path (replace with your actual path)
# file_path = 'golfDB_test/total/normalized_pose_data_4.json'
file_path = 'golfDB_json_data/wedge/combined_5_to_8.json'

# Load and process your data
data = load_data_from_json(file_path)
X_data, y_data = preprocess_data(data)

# Encode pose labels
encoder = LabelEncoder()
y_data_encoded = encoder.fit_transform(y_data)

# Convert labels to one-hot encoding
num_classes = len(np.unique(y_data))
y_data_one_hot = to_categorical(y_data_encoded, num_classes=num_classes)
print("num_classes",num_classes)
# Split the data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X_data, y_data_one_hot, test_size=0.2, random_state=42)

# Build a simple neural network model
model = Sequential([
    Dense(64, activation='relu', input_shape=(34,)),  # 34 input features
    Dropout(0.1),
    Dense(32, activation='relu'),
    Dropout(0.1),
    Dense(num_classes, activation='softmax')  # num_classes output classes
])

# Compile the model
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model
model.fit(X_train, y_train, epochs=25, batch_size=32, validation_split=0.2)

# Evaluate the model on the test set
test_loss, test_acc = model.evaluate(X_test, y_test)
print(f"Test accuracy: {test_acc}")

# Predict a new pose
def predict_pose(model, new_data):
    new_data = np.array([new_data])
    prediction = model.predict(new_data)
    predicted_pose_id = np.argmax(prediction)
    predicted_probability = np.max(prediction)
    return predicted_pose_id, predicted_probability

def normalize_pose_data(pose_data, reference_x=0.5572794732116567, reference_y=0.1998999040023779):
    normalized_data = []
    outliers = {}

    for pose_index, pose in enumerate(pose_data):
        keypoints = pose['Keypoints']
        nose_point = keypoints[0]  # First coordinate (nose)

        # Calculate offset to move nose coordinate to reference point
        offset_x = reference_x - nose_point['X']
        offset_y = reference_y - nose_point['Y']

        pose_outliers = {'X': 0, 'Y': 0, 'dirx':0, 'diry': 0}
        has_outliers = False

        # Apply offset to all coordinates and check for outliers
        for keypoint in keypoints:
            new_x = keypoint['X'] + offset_x
            new_y = keypoint['Y'] + offset_y

            if new_x < 0 or new_x > 1:
                pose_outliers['X'] += 1
                pose_outliers['dirx'] += new_x
                has_outliers = True
            if new_y < 0 or new_y > 1:
                pose_outliers['Y'] += 1
                pose_outliers['diry'] += new_y
                has_outliers = True

            keypoint['X'] = new_x
            keypoint['Y'] = new_y

        if not has_outliers:
            normalized_data.append(pose)
        else:
            outliers[pose_index] = pose_outliers

    return normalized_data, outliers

# Example input data for prediction (replace with actual data)
new_pose_data = [{
          "Pose": 1,
          "Keypoints": [
            {
              "Keypoint ID": 0,
              "Y": 0.1998999040023779,
              "X": 0.5572794732116567,
              "Confidence Score": 0.38429954648017883
            },
            {
              "Keypoint ID": 1,
              "Y": 0.1857140283481573,
              "X": 0.5674509760402547,
              "Confidence Score": 0.3766421675682068
            },
            {
              "Keypoint ID": 2,
              "Y": 0.18855988191528072,
              "X": 0.5435571428798543,
              "Confidence Score": 0.3990709185600281
            },
            {
              "Keypoint ID": 3,
              "Y": 0.1848350982562994,
              "X": 0.5841666516326772,
              "Confidence Score": 0.5482219457626343
            },
            {
              "Keypoint ID": 4,
              "Y": 0.19071208642883053,
              "X": 0.5350731071494924,
              "Confidence Score": 0.5129073262214661
            },
            {
              "Keypoint ID": 5,
              "Y": 0.24788459347648373,
              "X": 0.6238423046134817,
              "Confidence Score": 0.5817942023277283
            },
            {
              "Keypoint ID": 6,
              "Y": 0.2511663358108496,
              "X": 0.5107928272746908,
              "Confidence Score": 0.5316048860549927
            },
            {
              "Keypoint ID": 7,
              "Y": 0.3229065756694769,
              "X": 0.6461649593376028,
              "Confidence Score": 0.3576698303222656
            },
            {
              "Keypoint ID": 8,
              "Y": 0.32904674815101376,
              "X": 0.5030016657375204,
              "Confidence Score": 0.23619356751441956
            },
            {
              "Keypoint ID": 9,
              "Y": 0.3073511342899298,
              "X": 0.6697701868080007,
              "Confidence Score": 0.4405936896800995
            },
            {
              "Keypoint ID": 10,
              "Y": 0.391438684930036,
              "X": 0.5274413880370962,
              "Confidence Score": 0.124388687312603
            },
            {
              "Keypoint ID": 11,
              "Y": 0.4263933520214056,
              "X": 0.5869002398513662,
              "Confidence Score": 0.5152628421783447
            },
            {
              "Keypoint ID": 12,
              "Y": 0.4233699064151739,
              "X": 0.5177237745784627,
              "Confidence Score": 0.29457661509513855
            },
            {
              "Keypoint ID": 13,
              "Y": 0.5784742455379461,
              "X": 0.6054537352584707,
              "Confidence Score": 0.58955317735672
            },
            {
              "Keypoint ID": 14,
              "Y": 0.5684495191471075,
              "X": 0.4699011501335012,
              "Confidence Score": 0.333624929189682
            },
            {
              "Keypoint ID": 15,
              "Y": 0.7090776185886358,
              "X": 0.6185544785522329,
              "Confidence Score": 0.44528064131736755
            },
            {
              "Keypoint ID": 16,
              "Y": 0.691163740624616,
              "X": 0.4439542349838125,
              "Confidence Score": 0.6086346507072449
            }
          ]
        },
         {
          "Pose": 2,
          "Keypoints": [
            {
              "Keypoint ID": 0,
              "Y": 0.1998999040023779,
              "X": 0.5572794732116567,
              "Confidence Score": 0.28372180461883545
            },
            {
              "Keypoint ID": 1,
              "Y": 0.19283156799239864,
              "X": 0.5516909715198385,
              "Confidence Score": 0.251054048538208
            },
            {
              "Keypoint ID": 2,
              "Y": 0.19400509404105892,
              "X": 0.5688723978065359,
              "Confidence Score": 0.20210325717926025
            },
            {
              "Keypoint ID": 3,
              "Y": 0.18713878797454586,
              "X": 0.5563201066516744,
              "Confidence Score": 0.4916621148586273
            },
            {
              "Keypoint ID": 4,
              "Y": 0.1869665007488226,
              "X": 0.5949060079120504,
              "Confidence Score": 0.45228540897369385
            },
            {
              "Keypoint ID": 5,
              "Y": 0.22883694576186886,
              "X": 0.5502192136310445,
              "Confidence Score": 0.46836769580841064
            },
            {
              "Keypoint ID": 6,
              "Y": 0.22359960483474484,
              "X": 0.6151763853095876,
              "Confidence Score": 0.5013452172279358
            },
            {
              "Keypoint ID": 7,
              "Y": 0.3095289389984106,
              "X": 0.5179182943366872,
              "Confidence Score": 0.42813655734062195
            },
            {
              "Keypoint ID": 8,
              "Y": 0.2953772466079687,
              "X": 0.6203050073646413,
              "Confidence Score": 0.3206494152545929
            },
            {
              "Keypoint ID": 9,
              "Y": 0.3581000487701391,
              "X": 0.5069270190261709,
              "Confidence Score": 0.4132034182548523
            },
            {
              "Keypoint ID": 10,
              "Y": 0.344024054278562,
              "X": 0.5395278390907156,
              "Confidence Score": 0.29419827461242676
            },
            {
              "Keypoint ID": 11,
              "Y": 0.35305248903197994,
              "X": 0.5664144214652883,
              "Confidence Score": 0.5243645906448364
            },
            {
              "Keypoint ID": 12,
              "Y": 0.3505733530418371,
              "X": 0.6199239548705923,
              "Confidence Score": 0.5773006081581116
            },
            {
              "Keypoint ID": 13,
              "Y": 0.4603362004653906,
              "X": 0.5355464574359762,
              "Confidence Score": 0.5046972036361694
            },
            {
              "Keypoint ID": 14,
              "Y": 0.46579509185714474,
              "X": 0.6434544977210866,
              "Confidence Score": 0.5903673768043518
            },
            {
              "Keypoint ID": 15,
              "Y": 0.5729835550682043,
              "X": 0.5185484048389303,
              "Confidence Score": 0.6058805584907532
            },
            {
              "Keypoint ID": 16,
              "Y": 0.5775273959533667,
              "X": 0.6776927169822561,
              "Confidence Score": 0.5113898515701294
            }
          ]
        },
          {
   "Pose": 2,
   "Keypoints": [
             {
               "Keypoint ID": 0,
               "Y": 0.1998999040023779,
               "X": 0.5572794732116567,
               "Confidence Score": 0.18655680119991302
             },
             {
               "Keypoint ID": 1,
               "Y": 0.18478064941329708,
               "X": 0.5567325111888753,
               "Confidence Score": 0.16369657218456268
             },
             {
               "Keypoint ID": 2,
               "Y": 0.193505517710874,
               "X": 0.5570587870143758,
               "Confidence Score": 0.12436198443174362
             },
             {
               "Keypoint ID": 3,
               "Y": 0.1916620652572607,
               "X": 0.5737201627754079,
               "Confidence Score": 0.16603250801563263
             },
             {
               "Keypoint ID": 4,
               "Y": 0.19272985266608944,
               "X": 0.5685089584850179,
               "Confidence Score": 0.12152981013059616
             },
             {
               "Keypoint ID": 5,
               "Y": 0.23885490702552548,
               "X": 0.5913252290748464,
               "Confidence Score": 0.201650470495224
             },
             {
               "Keypoint ID": 6,
               "Y": 0.237171791066358,
               "X": 0.5663241800330984,
               "Confidence Score": 0.20409967005252838
             },
             {
               "Keypoint ID": 7,
               "Y": 0.2890136461154913,
               "X": 0.5921955760978567,
               "Confidence Score": 0.1201537474989891
             },
             {
               "Keypoint ID": 8,
               "Y": 0.28425227807922115,
               "X": 0.5303763803504812,
               "Confidence Score": 0.22033177316188812
             },
             {
               "Keypoint ID": 9,
               "Y": 0.3697345178024267,
               "X": 0.589822536375414,
               "Confidence Score": 0.08296327292919159
             },
             {
               "Keypoint ID": 10,
               "Y": 0.2914862553970312,
               "X": 0.52138197984923,
               "Confidence Score": 0.16009913384914398
             },
             {
               "Keypoint ID": 11,
               "Y": 0.3671037475959753,
               "X": 0.6054006275199758,
               "Confidence Score": 0.23828662931919098
             },
             {
               "Keypoint ID": 12,
               "Y": 0.366550258864591,
               "X": 0.5604556855224477,
               "Confidence Score": 0.28221383690834045
             },
             {
               "Keypoint ID": 13,
               "Y": 0.48618733095092526,
               "X": 0.6517440732978689,
               "Confidence Score": 0.28772029280662537
             },
             {
               "Keypoint ID": 14,
               "Y": 0.4802650730506872,
               "X": 0.5336893257163869,
               "Confidence Score": 0.3861292600631714
             },
             {
               "Keypoint ID": 15,
               "Y": 0.5927140037910437,
               "X": 0.6839636620544302,
               "Confidence Score": 0.3717656135559082
             },
             {
               "Keypoint ID": 16,
               "Y": 0.5978851239578222,
               "X": 0.5213201102279531,
               "Confidence Score": 0.5491869449615479
             }
           ]
         },
        {
        "Pose": 3,
        "Keypoints": [
          {
               "Keypoint ID": 0,
               "Y": 0.1998999040023779,
               "X": 0.5572794732116567,
               "Confidence Score": 0.5233508944511414
             },
             {
               "Keypoint ID": 1,
               "Y": 0.19005422996444454,
               "X": 0.5670533534549581,
               "Confidence Score": 0.41108906269073486
             },
             {
               "Keypoint ID": 2,
               "Y": 0.19183265375060787,
               "X": 0.5488169547580587,
               "Confidence Score": 0.41785308718681335
             },
             {
               "Keypoint ID": 3,
               "Y": 0.1872251551048254,
               "X": 0.5829964038394796,
               "Confidence Score": 0.359442800283432
             },
             {
               "Keypoint ID": 4,
               "Y": 0.18872528480453243,
               "X": 0.5425327178500997,
               "Confidence Score": 0.3397250175476074
             },
             {
               "Keypoint ID": 5,
               "Y": 0.22597106503410092,
               "X": 0.5999031421207296,
               "Confidence Score": 0.36322763562202454
             },
             {
               "Keypoint ID": 6,
               "Y": 0.22566648529929867,
               "X": 0.5411074515842306,
               "Confidence Score": 0.5271771550178528
             },
             {
               "Keypoint ID": 7,
               "Y": 0.27333658145828,
               "X": 0.5597523805164205,
               "Confidence Score": 0.33303192257881165
             },
             {
               "Keypoint ID": 8,
               "Y": 0.2595299999610876,
               "X": 0.4938227888606893,
               "Confidence Score": 0.3716002404689789
             },
             {
               "Keypoint ID": 9,
               "Y": 0.2674013893501257,
               "X": 0.4826879855655538,
               "Confidence Score": 0.22656208276748657
             },
             {
               "Keypoint ID": 10,
               "Y": 0.2588499109642004,
               "X": 0.4175957795642721,
               "Confidence Score": 0.3326752185821533
             },
             {
               "Keypoint ID": 11,
               "Y": 0.3651062767402624,
               "X": 0.6247091647647726,
               "Confidence Score": 0.6366832256317139
             },
             {
               "Keypoint ID": 12,
               "Y": 0.36474507259292355,
               "X": 0.5685849544071065,
               "Confidence Score": 0.6100196838378906
             },
             {
               "Keypoint ID": 13,
               "Y": 0.4840913932220434,
               "X": 0.6307024117969381,
               "Confidence Score": 0.5793138146400452
             },
             {
               "Keypoint ID": 14,
               "Y": 0.47386037515563717,
               "X": 0.5469901320003377,
               "Confidence Score": 0.4684992730617523
             },
             {
               "Keypoint ID": 15,
               "Y": 0.6038166205780005,
               "X": 0.6602253076099264,
               "Confidence Score": 0.614835798740387
             },
             {
               "Keypoint ID": 16,
               "Y": 0.6002893965141272,
               "X": 0.5348793026470052,
               "Confidence Score": 0.6604465842247009
             }
        ]
      },
     {
      "Pose": 4,
      "Keypoints": [
        {
          "Keypoint ID": 0,
          "Y": 0.1998999040023779,
          "X": 0.5572794732116567,
          "Confidence Score": 0.3467405438423157
        },
        {
          "Keypoint ID": 1,
          "Y": 0.19532193945808163,
          "X": 0.5606731232665884,
          "Confidence Score": 0.3797306716442108
        },
        {
          "Keypoint ID": 2,
          "Y": 0.19583689378661862,
          "X": 0.551107412245165,
          "Confidence Score": 0.3314727246761322
        },
        {
          "Keypoint ID": 3,
          "Y": 0.19690873431129208,
          "X": 0.577030902769457,
          "Confidence Score": 0.45247089862823486
        },
        {
          "Keypoint ID": 4,
          "Y": 0.19540642904205074,
          "X": 0.5503422376178609,
          "Confidence Score": 0.2488090842962265
        },
        {
          "Keypoint ID": 5,
          "Y": 0.23554625319404354,
          "X": 0.597602671053301,
          "Confidence Score": 0.4830474555492401
        },
        {
          "Keypoint ID": 6,
          "Y": 0.2300909976856207,
          "X": 0.5393918808959829,
          "Confidence Score": 0.4640575051307678
        },
        {
          "Keypoint ID": 7,
          "Y": 0.2597375433341955,
          "X": 0.5990965422653066,
          "Confidence Score": 0.23661795258522034
        },
        {
          "Keypoint ID": 8,
          "Y": 0.22349279331130734,
          "X": 0.4972584303878652,
          "Confidence Score": 0.2514112591743469
        },
        {
          "Keypoint ID": 9,
          "Y": 0.18169014858169308,
          "X": 0.4865576383136617,
          "Confidence Score": 0.48414140939712524
        },
        {
          "Keypoint ID": 10,
          "Y": 0.18301441477699032,
          "X": 0.4750656243823873,
          "Confidence Score": 0.3429151177406311
        },
        {
          "Keypoint ID": 11,
          "Y": 0.3608725588218664,
          "X": 0.6029389556907522,
          "Confidence Score": 0.5062991380691528
        },
        {
          "Keypoint ID": 12,
          "Y": 0.36061065601272335,
          "X": 0.5471519288085805,
          "Confidence Score": 0.5095577239990234
        },
        {
          "Keypoint ID": 13,
          "Y": 0.45916622089309445,
          "X": 0.6069391426109182,
          "Confidence Score": 0.45024603605270386
        },
        {
          "Keypoint ID": 14,
          "Y": 0.45999669240874996,
          "X": 0.542729144956957,
          "Confidence Score": 0.3652518093585968
        },
        {
          "Keypoint ID": 15,
          "Y": 0.5711054127113318,
          "X": 0.641198759939562,
          "Confidence Score": 0.5267818570137024
        },
        {
          "Keypoint ID": 16,
          "Y": 0.5709175388709997,
          "X": 0.5230086502097951,
          "Confidence Score": 0.40136680006980896
        }
      ]
    }
]

result1, result2 = normalize_pose_data(new_pose_data)
for k in range(len(new_pose_data)):
    new_data = result1[k]["Keypoints"]  # Using the first normalized pose
    new_pose_features = [kp["X"] for kp in new_data] + [kp["Y"] for kp in new_data]
    predicted_pose_id, predicted_probability = predict_pose(model, new_pose_features)
    print(f"Predicted Pose ID: {predicted_pose_id}, Probability: {predicted_probability}")

# Save the model in TensorFlow format (HDF5 format)
model.save('golfDB_json_data/wedge/pose_classification_model_8.h5')

# Convert to TensorFlow Lite
converter = tf.lite.TFLiteConverter.from_keras_model(model)
tflite_model = converter.convert()
with open("golfDB_json_data/wedge/pose_classifier_8.tflite", "wb") as f:
    f.write(tflite_model)

# Function to convert saved model to TFLite
def convert_to_tflite(model_path, output_tflite_path):
    model = tf.keras.models.load_model(model_path)
    converter = tf.lite.TFLiteConverter.from_keras_model(model)
    tflite_model = converter.convert()
    with open(output_tflite_path, 'wb') as f:
        f.write(tflite_model)

# Convert and save the TFLite model
convert_to_tflite('golfDB_json_data/wedge/pose_classification_model_8.h5', 'golfDB_json_data/wedge/pose_classification_model_8.tflite')

num_classes 4
Epoch 1/25


/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - accuracy: 0.2963 - loss: 1.4474 - val_accuracy: 0.4286 - val_loss: 1.4078
Epoch 2/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 121ms/step - accuracy: 0.2593 - loss: 1.4155 - val_accuracy: 0.1429 - val_loss: 1.4089
Epoch 3/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step - accuracy: 0.2593 - loss: 1.4368 - val_accuracy: 0.1429 - val_loss: 1.4082
Epoch 4/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step - accuracy: 0.2222 - loss: 1.4274 - val_accuracy: 0.1429 - val_loss: 1.4072
Epoch 5/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 65ms/step - accuracy: 0.2593 - loss: 1.3990 - val_accuracy: 0.1429 - val_loss: 1.4072
Epoch 6/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step - accuracy: 0.2963 - loss: 1.4256 - val_accuracy: 0.1429 - val_loss: 1.4084
Epoch 7/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 59ms/step - accuracy: 0.2963 - loss: 1.4310 - val_accuracy: 0.1429 - val_loss: 1.4097
Epoch 8/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step - accuracy: 0.3333 - loss: 1.3940 - val_accuracy: 0.1429 - val_loss: 1.4112
Epoch 9/25
1

Predicted Pose ID: 2, Probability: 0.2736816704273224
Saved artifact at '/tmp/tmph6vesr33'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='keras_tensor_222')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  132313550454480: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313550229344: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313550235680: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313550239552: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313550233040: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313550241488: TensorSpec(shape=(), dtype=tf.resource, name=None)


Saved artifact at '/tmp/tmpwxx9436w'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='input_layer_12')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  132313546116080: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313546288192: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313545392896: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313545395712: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313545398880: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132313545404864: TensorSpec(shape=(), dtype=tf.resource, name=None)


In [12]:
import numpy as np
import json
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical

# Function to load data from a JSON file
def load_data_from_json(file_path):
    with open(file_path, 'r') as file:
        data = json.load(file)
    return data

# Function to preprocess the data
def preprocess_data(data):
    X = []
    y = []

    for entry in data:
        pose_id = entry["Pose"]
        keypoints = entry["Keypoints"]

        # Extract X and Y coordinates
        x_coords = [kp["X"] for kp in keypoints]
        y_coords = [kp["Y"] for kp in keypoints]

        # Combine X and Y into a single feature vector
        features = x_coords + y_coords  # 17 keypoints = 34 features (17x2)
        X.append(features)
        y.append(pose_id)

    return np.array(X), np.array(y)

# File path to the dataset
file_path = 'golfDB_json_data/wedge/combined_5_to_8.json'

# Load and process your data
data = load_data_from_json(file_path)
X_data, y_data = preprocess_data(data)

# Encode the pose labels (e.g., 0 to 3 for 4 poses)
encoder = LabelEncoder()
y_data_encoded = encoder.fit_transform(y_data)

# Convert labels to one-hot encoding for categorical classification
num_classes = len(np.unique(y_data))  # Should be 4 for 4 poses
y_data_one_hot = to_categorical(y_data_encoded, num_classes=num_classes)
print("num_classes:", num_classes)

# Split the dataset into training and test sets (80% train, 20% test)
X_train, X_test, y_train, y_test = train_test_split(X_data, y_data_one_hot, test_size=0.2, random_state=42)

# Build a simple MLP model
# model = Sequential([
#     Dense(64, activation='relu', input_shape=(34,)),  # 34 input features (17x2 for X and Y)
#     Dropout(0.1),  # Dropout to prevent overfitting
#     Dense(32, activation='relu'),  # Second hidden layer
#     Dropout(0.1),
#     Dense(num_classes, activation='softmax')  # Output layer (softmax for multi-class classification)
# ])
model = Sequential([
    Dense(256, activation='relu', input_shape=(34,), kernel_regularizer=l2(0.001)),  # First hidden layer with L2 regularization
    BatchNormalization(),  # Batch normalization for better training
    Dropout(0.2),  # Increased dropout to 0.2 to avoid overfitting
    Dense(128, activation='relu', kernel_regularizer=l2(0.001)),  # Second hidden layer
    BatchNormalization(),
    Dropout(0.3),  # More aggressive dropout for regularization
    Dense(64, activation='relu', kernel_regularizer=l2(0.001)),  # Third hidden layer
    BatchNormalization(),
    Dropout(0.3),
    Dense(32, activation='relu', kernel_regularizer=l2(0.001)),  # Fourth hidden layer
    Dropout(0.4),
    Dense(num_classes, activation='softmax')  # Output layer for classification
])

# Compile the model with Adam optimizer and categorical cross-entropy loss
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model on the training set
model.fit(X_train, y_train, epochs=25, batch_size=32, validation_split=0.2)

# Evaluate the model on the test set
test_loss, test_acc = model.evaluate(X_test, y_test)
print(f"Test accuracy: {test_acc}")

# Function to predict a pose from new data
def predict_pose(model, new_data):
    new_data = np.array([new_data])  # Convert input to numpy array
    prediction = model.predict(new_data)
    predicted_pose_id = np.argmax(prediction)  # Get the class with highest probability
    predicted_probability = np.max(prediction)  # Get the highest probability
    return predicted_pose_id, predicted_probability

# Normalize pose data function (already provided)
def normalize_pose_data(pose_data, reference_x=0.5572794732116567, reference_y=0.1998999040023779):
    normalized_data = []
    outliers = {}

    for pose_index, pose in enumerate(pose_data):
        keypoints = pose['Keypoints']
        nose_point = keypoints[0]  # Assume the first keypoint is the nose

        # Offset to align the nose with reference point
        offset_x = reference_x - nose_point['X']
        offset_y = reference_y - nose_point['Y']

        pose_outliers = {'X': 0, 'Y': 0, 'dirx': 0, 'diry': 0}
        has_outliers = False

        # Adjust each keypoint by offset
        for keypoint in keypoints:
            new_x = keypoint['X'] + offset_x
            new_y = keypoint['Y'] + offset_y

            if new_x < 0 or new_x > 1:
                pose_outliers['X'] += 1
                pose_outliers['dirx'] += new_x
                has_outliers = True
            if new_y < 0 or new_y > 1:
                pose_outliers['Y'] += 1
                pose_outliers['diry'] += new_y
                has_outliers = True

            keypoint['X'] = new_x
            keypoint['Y'] = new_y

        if not has_outliers:
            normalized_data.append(pose)
        else:
            outliers[pose_index] = pose_outliers

    return normalized_data, outliers

# Example input data for prediction (replace with actual data)
new_pose_data = [{
          "Pose": 1,
          "Keypoints": [
            {
              "Keypoint ID": 0,
              "Y": 0.1998999040023779,
              "X": 0.5572794732116567,
              "Confidence Score": 0.38429954648017883
            },
            {
              "Keypoint ID": 1,
              "Y": 0.1857140283481573,
              "X": 0.5674509760402547,
              "Confidence Score": 0.3766421675682068
            },
            {
              "Keypoint ID": 2,
              "Y": 0.18855988191528072,
              "X": 0.5435571428798543,
              "Confidence Score": 0.3990709185600281
            },
            {
              "Keypoint ID": 3,
              "Y": 0.1848350982562994,
              "X": 0.5841666516326772,
              "Confidence Score": 0.5482219457626343
            },
            {
              "Keypoint ID": 4,
              "Y": 0.19071208642883053,
              "X": 0.5350731071494924,
              "Confidence Score": 0.5129073262214661
            },
            {
              "Keypoint ID": 5,
              "Y": 0.24788459347648373,
              "X": 0.6238423046134817,
              "Confidence Score": 0.5817942023277283
            },
            {
              "Keypoint ID": 6,
              "Y": 0.2511663358108496,
              "X": 0.5107928272746908,
              "Confidence Score": 0.5316048860549927
            },
            {
              "Keypoint ID": 7,
              "Y": 0.3229065756694769,
              "X": 0.6461649593376028,
              "Confidence Score": 0.3576698303222656
            },
            {
              "Keypoint ID": 8,
              "Y": 0.32904674815101376,
              "X": 0.5030016657375204,
              "Confidence Score": 0.23619356751441956
            },
            {
              "Keypoint ID": 9,
              "Y": 0.3073511342899298,
              "X": 0.6697701868080007,
              "Confidence Score": 0.4405936896800995
            },
            {
              "Keypoint ID": 10,
              "Y": 0.391438684930036,
              "X": 0.5274413880370962,
              "Confidence Score": 0.124388687312603
            },
            {
              "Keypoint ID": 11,
              "Y": 0.4263933520214056,
              "X": 0.5869002398513662,
              "Confidence Score": 0.5152628421783447
            },
            {
              "Keypoint ID": 12,
              "Y": 0.4233699064151739,
              "X": 0.5177237745784627,
              "Confidence Score": 0.29457661509513855
            },
            {
              "Keypoint ID": 13,
              "Y": 0.5784742455379461,
              "X": 0.6054537352584707,
              "Confidence Score": 0.58955317735672
            },
            {
              "Keypoint ID": 14,
              "Y": 0.5684495191471075,
              "X": 0.4699011501335012,
              "Confidence Score": 0.333624929189682
            },
            {
              "Keypoint ID": 15,
              "Y": 0.7090776185886358,
              "X": 0.6185544785522329,
              "Confidence Score": 0.44528064131736755
            },
            {
              "Keypoint ID": 16,
              "Y": 0.691163740624616,
              "X": 0.4439542349838125,
              "Confidence Score": 0.6086346507072449
            }
          ]
        },
         {
          "Pose": 2,
          "Keypoints": [
            {
              "Keypoint ID": 0,
              "Y": 0.1998999040023779,
              "X": 0.5572794732116567,
              "Confidence Score": 0.28372180461883545
            },
            {
              "Keypoint ID": 1,
              "Y": 0.19283156799239864,
              "X": 0.5516909715198385,
              "Confidence Score": 0.251054048538208
            },
            {
              "Keypoint ID": 2,
              "Y": 0.19400509404105892,
              "X": 0.5688723978065359,
              "Confidence Score": 0.20210325717926025
            },
            {
              "Keypoint ID": 3,
              "Y": 0.18713878797454586,
              "X": 0.5563201066516744,
              "Confidence Score": 0.4916621148586273
            },
            {
              "Keypoint ID": 4,
              "Y": 0.1869665007488226,
              "X": 0.5949060079120504,
              "Confidence Score": 0.45228540897369385
            },
            {
              "Keypoint ID": 5,
              "Y": 0.22883694576186886,
              "X": 0.5502192136310445,
              "Confidence Score": 0.46836769580841064
            },
            {
              "Keypoint ID": 6,
              "Y": 0.22359960483474484,
              "X": 0.6151763853095876,
              "Confidence Score": 0.5013452172279358
            },
            {
              "Keypoint ID": 7,
              "Y": 0.3095289389984106,
              "X": 0.5179182943366872,
              "Confidence Score": 0.42813655734062195
            },
            {
              "Keypoint ID": 8,
              "Y": 0.2953772466079687,
              "X": 0.6203050073646413,
              "Confidence Score": 0.3206494152545929
            },
            {
              "Keypoint ID": 9,
              "Y": 0.3581000487701391,
              "X": 0.5069270190261709,
              "Confidence Score": 0.4132034182548523
            },
            {
              "Keypoint ID": 10,
              "Y": 0.344024054278562,
              "X": 0.5395278390907156,
              "Confidence Score": 0.29419827461242676
            },
            {
              "Keypoint ID": 11,
              "Y": 0.35305248903197994,
              "X": 0.5664144214652883,
              "Confidence Score": 0.5243645906448364
            },
            {
              "Keypoint ID": 12,
              "Y": 0.3505733530418371,
              "X": 0.6199239548705923,
              "Confidence Score": 0.5773006081581116
            },
            {
              "Keypoint ID": 13,
              "Y": 0.4603362004653906,
              "X": 0.5355464574359762,
              "Confidence Score": 0.5046972036361694
            },
            {
              "Keypoint ID": 14,
              "Y": 0.46579509185714474,
              "X": 0.6434544977210866,
              "Confidence Score": 0.5903673768043518
            },
            {
              "Keypoint ID": 15,
              "Y": 0.5729835550682043,
              "X": 0.5185484048389303,
              "Confidence Score": 0.6058805584907532
            },
            {
              "Keypoint ID": 16,
              "Y": 0.5775273959533667,
              "X": 0.6776927169822561,
              "Confidence Score": 0.5113898515701294
            }
          ]
        },
          {
   "Pose": 2,
   "Keypoints": [
             {
               "Keypoint ID": 0,
               "Y": 0.1998999040023779,
               "X": 0.5572794732116567,
               "Confidence Score": 0.18655680119991302
             },
             {
               "Keypoint ID": 1,
               "Y": 0.18478064941329708,
               "X": 0.5567325111888753,
               "Confidence Score": 0.16369657218456268
             },
             {
               "Keypoint ID": 2,
               "Y": 0.193505517710874,
               "X": 0.5570587870143758,
               "Confidence Score": 0.12436198443174362
             },
             {
               "Keypoint ID": 3,
               "Y": 0.1916620652572607,
               "X": 0.5737201627754079,
               "Confidence Score": 0.16603250801563263
             },
             {
               "Keypoint ID": 4,
               "Y": 0.19272985266608944,
               "X": 0.5685089584850179,
               "Confidence Score": 0.12152981013059616
             },
             {
               "Keypoint ID": 5,
               "Y": 0.23885490702552548,
               "X": 0.5913252290748464,
               "Confidence Score": 0.201650470495224
             },
             {
               "Keypoint ID": 6,
               "Y": 0.237171791066358,
               "X": 0.5663241800330984,
               "Confidence Score": 0.20409967005252838
             },
             {
               "Keypoint ID": 7,
               "Y": 0.2890136461154913,
               "X": 0.5921955760978567,
               "Confidence Score": 0.1201537474989891
             },
             {
               "Keypoint ID": 8,
               "Y": 0.28425227807922115,
               "X": 0.5303763803504812,
               "Confidence Score": 0.22033177316188812
             },
             {
               "Keypoint ID": 9,
               "Y": 0.3697345178024267,
               "X": 0.589822536375414,
               "Confidence Score": 0.08296327292919159
             },
             {
               "Keypoint ID": 10,
               "Y": 0.2914862553970312,
               "X": 0.52138197984923,
               "Confidence Score": 0.16009913384914398
             },
             {
               "Keypoint ID": 11,
               "Y": 0.3671037475959753,
               "X": 0.6054006275199758,
               "Confidence Score": 0.23828662931919098
             },
             {
               "Keypoint ID": 12,
               "Y": 0.366550258864591,
               "X": 0.5604556855224477,
               "Confidence Score": 0.28221383690834045
             },
             {
               "Keypoint ID": 13,
               "Y": 0.48618733095092526,
               "X": 0.6517440732978689,
               "Confidence Score": 0.28772029280662537
             },
             {
               "Keypoint ID": 14,
               "Y": 0.4802650730506872,
               "X": 0.5336893257163869,
               "Confidence Score": 0.3861292600631714
             },
             {
               "Keypoint ID": 15,
               "Y": 0.5927140037910437,
               "X": 0.6839636620544302,
               "Confidence Score": 0.3717656135559082
             },
             {
               "Keypoint ID": 16,
               "Y": 0.5978851239578222,
               "X": 0.5213201102279531,
               "Confidence Score": 0.5491869449615479
             }
           ]
         },
        {
        "Pose": 3,
        "Keypoints": [
          {
               "Keypoint ID": 0,
               "Y": 0.1998999040023779,
               "X": 0.5572794732116567,
               "Confidence Score": 0.5233508944511414
             },
             {
               "Keypoint ID": 1,
               "Y": 0.19005422996444454,
               "X": 0.5670533534549581,
               "Confidence Score": 0.41108906269073486
             },
             {
               "Keypoint ID": 2,
               "Y": 0.19183265375060787,
               "X": 0.5488169547580587,
               "Confidence Score": 0.41785308718681335
             },
             {
               "Keypoint ID": 3,
               "Y": 0.1872251551048254,
               "X": 0.5829964038394796,
               "Confidence Score": 0.359442800283432
             },
             {
               "Keypoint ID": 4,
               "Y": 0.18872528480453243,
               "X": 0.5425327178500997,
               "Confidence Score": 0.3397250175476074
             },
             {
               "Keypoint ID": 5,
               "Y": 0.22597106503410092,
               "X": 0.5999031421207296,
               "Confidence Score": 0.36322763562202454
             },
             {
               "Keypoint ID": 6,
               "Y": 0.22566648529929867,
               "X": 0.5411074515842306,
               "Confidence Score": 0.5271771550178528
             },
             {
               "Keypoint ID": 7,
               "Y": 0.27333658145828,
               "X": 0.5597523805164205,
               "Confidence Score": 0.33303192257881165
             },
             {
               "Keypoint ID": 8,
               "Y": 0.2595299999610876,
               "X": 0.4938227888606893,
               "Confidence Score": 0.3716002404689789
             },
             {
               "Keypoint ID": 9,
               "Y": 0.2674013893501257,
               "X": 0.4826879855655538,
               "Confidence Score": 0.22656208276748657
             },
             {
               "Keypoint ID": 10,
               "Y": 0.2588499109642004,
               "X": 0.4175957795642721,
               "Confidence Score": 0.3326752185821533
             },
             {
               "Keypoint ID": 11,
               "Y": 0.3651062767402624,
               "X": 0.6247091647647726,
               "Confidence Score": 0.6366832256317139
             },
             {
               "Keypoint ID": 12,
               "Y": 0.36474507259292355,
               "X": 0.5685849544071065,
               "Confidence Score": 0.6100196838378906
             },
             {
               "Keypoint ID": 13,
               "Y": 0.4840913932220434,
               "X": 0.6307024117969381,
               "Confidence Score": 0.5793138146400452
             },
             {
               "Keypoint ID": 14,
               "Y": 0.47386037515563717,
               "X": 0.5469901320003377,
               "Confidence Score": 0.4684992730617523
             },
             {
               "Keypoint ID": 15,
               "Y": 0.6038166205780005,
               "X": 0.6602253076099264,
               "Confidence Score": 0.614835798740387
             },
             {
               "Keypoint ID": 16,
               "Y": 0.6002893965141272,
               "X": 0.5348793026470052,
               "Confidence Score": 0.6604465842247009
             }
        ]
      },
     {
      "Pose": 4,
      "Keypoints": [
        {
          "Keypoint ID": 0,
          "Y": 0.1998999040023779,
          "X": 0.5572794732116567,
          "Confidence Score": 0.3467405438423157
        },
        {
          "Keypoint ID": 1,
          "Y": 0.19532193945808163,
          "X": 0.5606731232665884,
          "Confidence Score": 0.3797306716442108
        },
        {
          "Keypoint ID": 2,
          "Y": 0.19583689378661862,
          "X": 0.551107412245165,
          "Confidence Score": 0.3314727246761322
        },
        {
          "Keypoint ID": 3,
          "Y": 0.19690873431129208,
          "X": 0.577030902769457,
          "Confidence Score": 0.45247089862823486
        },
        {
          "Keypoint ID": 4,
          "Y": 0.19540642904205074,
          "X": 0.5503422376178609,
          "Confidence Score": 0.2488090842962265
        },
        {
          "Keypoint ID": 5,
          "Y": 0.23554625319404354,
          "X": 0.597602671053301,
          "Confidence Score": 0.4830474555492401
        },
        {
          "Keypoint ID": 6,
          "Y": 0.2300909976856207,
          "X": 0.5393918808959829,
          "Confidence Score": 0.4640575051307678
        },
        {
          "Keypoint ID": 7,
          "Y": 0.2597375433341955,
          "X": 0.5990965422653066,
          "Confidence Score": 0.23661795258522034
        },
        {
          "Keypoint ID": 8,
          "Y": 0.22349279331130734,
          "X": 0.4972584303878652,
          "Confidence Score": 0.2514112591743469
        },
        {
          "Keypoint ID": 9,
          "Y": 0.18169014858169308,
          "X": 0.4865576383136617,
          "Confidence Score": 0.48414140939712524
        },
        {
          "Keypoint ID": 10,
          "Y": 0.18301441477699032,
          "X": 0.4750656243823873,
          "Confidence Score": 0.3429151177406311
        },
        {
          "Keypoint ID": 11,
          "Y": 0.3608725588218664,
          "X": 0.6029389556907522,
          "Confidence Score": 0.5062991380691528
        },
        {
          "Keypoint ID": 12,
          "Y": 0.36061065601272335,
          "X": 0.5471519288085805,
          "Confidence Score": 0.5095577239990234
        },
        {
          "Keypoint ID": 13,
          "Y": 0.45916622089309445,
          "X": 0.6069391426109182,
          "Confidence Score": 0.45024603605270386
        },
        {
          "Keypoint ID": 14,
          "Y": 0.45999669240874996,
          "X": 0.542729144956957,
          "Confidence Score": 0.3652518093585968
        },
        {
          "Keypoint ID": 15,
          "Y": 0.5711054127113318,
          "X": 0.641198759939562,
          "Confidence Score": 0.5267818570137024
        },
        {
          "Keypoint ID": 16,
          "Y": 0.5709175388709997,
          "X": 0.5230086502097951,
          "Confidence Score": 0.40136680006980896
        }
      ]
    }
]

# Example prediction on test data
new_pose_data = result1  # Replace this with your normalized test pose data
for k in range(len(new_pose_data)):
    new_data = result1[k]["Keypoints"]  # Use normalized pose
    new_pose_features = [kp["X"] for kp in new_data] + [kp["Y"] for kp in new_data]  # Create feature vector
    predicted_pose_id, predicted_probability = predict_pose(model, new_pose_features)
    print(f"Predicted Pose ID: {predicted_pose_id}, Probability: {predicted_probability}")

# Save the trained model to a file (HDF5 format)
model.save('golfDB_json_data/wedge/pose_classification_model_8.h5')

# Convert the saved model to TensorFlow Lite format
converter = tf.lite.TFLiteConverter.from_keras_model(model)
tflite_model = converter.convert()
with open("golfDB_json_data/wedge/pose_classifier_8.tflite", "wb") as f:
    f.write(tflite_model)

# Function to convert a saved model to TFLite
def convert_to_tflite(model_path, output_tflite_path):
    model = tf.keras.models.load_model(model_path)
    converter = tf.lite.TFLiteConverter.from_keras_model(model)
    tflite_model = converter.convert()
    with open(output_tflite_path, 'wb') as f:
        f.write(tflite_model)

# Convert and save the model as TFLite
convert_to_tflite('golfDB_json_data/wedge/pose_classification_model_8.h5', 'golfDB_json_data/wedge/pose_classification_model_8.tflite')


FileNotFoundError: [Errno 2] No such file or directory: 'golfDB_json_data/wedge/combined_5_to_8.json'

In [16]:
import numpy as np
import json
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, BatchNormalization
from tensorflow.keras.regularizers import l2
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical
import os

def load_data_from_json(file_path):
    with open(file_path, 'r') as file:
        data = json.load(file)
    return data

def preprocess_data(data):
    X = []
    y = []
    for entry in data:
        pose_id = entry["Pose"]
        keypoints = entry["Keypoints"]
        x_coords = [kp["X"] for kp in keypoints]
        y_coords = [kp["Y"] for kp in keypoints]
        features = x_coords + y_coords
        X.append(features)
        y.append(pose_id)
    return np.array(X), np.array(y)

def create_model(input_shape, num_classes):
    model = Sequential([
        Dense(256, activation='relu', input_shape=input_shape, kernel_regularizer=l2(0.001)),
        BatchNormalization(),
        Dropout(0.2),
        Dense(128, activation='relu', kernel_regularizer=l2(0.001)),
        BatchNormalization(),
        Dropout(0.3),
        Dense(64, activation='relu', kernel_regularizer=l2(0.001)),
        BatchNormalization(),
        Dropout(0.3),
        Dense(32, activation='relu', kernel_regularizer=l2(0.001)),
        Dropout(0.4),
        Dense(num_classes, activation='softmax')
    ])
    model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    return model

def train_and_save_model(club_type, data_path):
    print(f"Processing {club_type}...")

    # Load and preprocess data
    data = load_data_from_json(data_path)
    X_data, y_data = preprocess_data(data)

    # Encode labels
    encoder = LabelEncoder()
    y_data_encoded = encoder.fit_transform(y_data)
    num_classes = len(np.unique(y_data))
    y_data_one_hot = to_categorical(y_data_encoded, num_classes=num_classes)

    # Split data
    X_train, X_test, y_train, y_test = train_test_split(X_data, y_data_one_hot, test_size=0.2, random_state=42)

    # Create and train model
    model = create_model((34,), num_classes)
    model.fit(X_train, y_train, epochs=25, batch_size=32, validation_split=0.2, verbose=1)

    # Evaluate model
    test_loss, test_acc = model.evaluate(X_test, y_test, verbose=0)
    print(f"{club_type} - Test accuracy: {test_acc}")

    # Save model
    h5_path = f'json_data/{club_type}/pose_classification_model8.h5'
    tflite_path = f'json_data/{club_type}/pose_classification_model8.tflite'

    model.save(h5_path)

    # Convert to TFLite
    converter = tf.lite.TFLiteConverter.from_keras_model(model)
    tflite_model = converter.convert()
    with open(tflite_path, 'wb') as f:
        f.write(tflite_model)

    print(f"Model for {club_type} saved as {tflite_path}")

# Main execution
club_types = ['driver', 'fairway', 'hybrid', 'iron', 'wedge']

for club_type in club_types:
    data_path = f'json_data/{club_type}/combined_data8.json'
    if os.path.exists(data_path):
        train_and_save_model(club_type, data_path)
    else:
        print(f"Warning: Data file for {club_type} not found at {data_path}")

print("Processing completed for all available club types.")

Processing driver...
Epoch 1/25


/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


27/27 ━━━━━━━━━━━━━━━━━━━━ 4s 16ms/step - accuracy: 0.4098 - loss: 1.9041 - val_accuracy: 0.2347 - val_loss: 1.6895
Epoch 2/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.7009 - loss: 1.0391 - val_accuracy: 0.2770 - val_loss: 1.6375
Epoch 3/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.7438 - loss: 0.9743 - val_accuracy: 0.4178 - val_loss: 1.6020
Epoch 4/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8388 - loss: 0.7379 - val_accuracy: 0.4601 - val_loss: 1.5427
Epoch 5/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - accuracy: 0.8452 - loss: 0.7464 - val_accuracy: 0.6338 - val_loss: 1.4833
Epoch 6/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - accuracy: 0.8671 - loss: 0.7000 - val_accuracy: 0.2723 - val_loss: 1.4387
Epoch 7/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.8714 - loss: 0.6795 - val_accuracy: 0.4413 - val_loss: 1.3761
Epoch 8/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8665 - loss: 0.6767 - val_accuracy: 0.5634 - val_loss: 1.3453
Ep

driver - Test accuracy: 0.6917293071746826
Saved artifact at '/tmp/tmpj5yb2n8r'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='keras_tensor_65')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  134018830884480: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830888176: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830913024: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830912672: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830891872: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830910736: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830913376: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830918304: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830915664: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830919008: TensorSpec(shape=(), dtype=tf.

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


...

6/6 ━━━━━━━━━━━━━━━━━━━━ 4s 67ms/step - accuracy: 0.3105 - loss: 2.1298 - val_accuracy: 0.3111 - val_loss: 1.7332
Epoch 2/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.4882 - loss: 1.5546 - val_accuracy: 0.3333 - val_loss: 1.7137
Epoch 3/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.5269 - loss: 1.4238 - val_accuracy: 0.3556 - val_loss: 1.6955
Epoch 4/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6944 - loss: 1.1367 - val_accuracy: 0.6889 - val_loss: 1.6810
Epoch 5/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7022 - loss: 1.0478 - val_accuracy: 0.4000 - val_loss: 1.6672
Epoch 6/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - accuracy: 0.7679 - loss: 0.8891 - val_accuracy: 0.2222 - val_loss: 1.6572
Epoch 7/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7407 - loss: 0.9501 - val_accuracy: 0.2444 - val_loss: 1.6546
Epoch 8/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.8433 - loss: 0.7318 - val_accuracy: 0.2222 - val_loss: 1.6569
Epoch 9/25
6/6 

iron - Test accuracy: 0.42105263471603394
Saved artifact at '/tmp/tmp26lux4bd'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='keras_tensor_104')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  134018796846800: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796801888: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796810160: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796809808: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796805584: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796807872: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796811216: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796810512: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796849104: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018796847696: TensorSpec(shape=(), dtype=tf.

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


1/1 ━━━━━━━━━━━━━━━━━━━━ 4s 4s/step - accuracy: 0.2222 - loss: 2.4765 - val_accuracy: 0.2857 - val_loss: 1.7428
Epoch 2/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 358ms/step - accuracy: 0.2593 - loss: 2.3716 - val_accuracy: 0.2857 - val_loss: 1.7387
Epoch 3/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step - accuracy: 0.4444 - loss: 1.9797 - val_accuracy: 0.2857 - val_loss: 1.7336
Epoch 4/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step - accuracy: 0.3704 - loss: 1.8571 - val_accuracy: 0.2857 - val_loss: 1.7296
Epoch 5/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 73ms/step - accuracy: 0.2222 - loss: 2.0124 - val_accuracy: 0.2857 - val_loss: 1.7276
Epoch 6/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - accuracy: 0.3333 - loss: 1.9398 - val_accuracy: 0.1429 - val_loss: 1.7260
Epoch 7/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step - accuracy: 0.4444 - loss: 1.8079 - val_accuracy: 0.1429 - val_loss: 1.7213
Epoch 8/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - accuracy: 0.5926 - loss: 1.3574 - val_accuracy: 0.1429 - val_loss: 1.7167
Epoch 9/25
1

wedge - Test accuracy: 0.4444444477558136
Saved artifact at '/tmp/tmpdz8ln2ke'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='keras_tensor_117')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  134018830199344: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830193360: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830190368: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830188784: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830196880: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830204624: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830196704: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830097344: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830094704: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018830096640: TensorSpec(shape=(), dtype=tf.

In [ ]:
# json integration

In [ ]:
import json
import os
# golfDB_json_data
def load_json_file(file_path):
    """
    Load JSON data from a file.

    Args:
    - file_path (str): The path to the JSON file.

    Returns:
    - data (list or dict): The JSON data loaded from the file.
    """
    with open(file_path, 'r') as f:
        return json.load(f)

def combine_json_files(file_list):
    """
    Combine multiple JSON files into one list of poses and keypoints.

    Args:
    - file_list (list): List of paths to JSON files to combine.

    Returns:
    - combined_data (list): The combined list of poses and keypoints from all files.
    """
    combined_data = []

    for file_path in file_list:
        data = load_json_file(file_path)
        combined_data.extend(data)  # Assuming the data is a list of poses
        print(f"Loaded data from {file_path}")

    return combined_data

# Usage:
folders = ['driver', 'fairway', 'hybird', 'iron', 'wedge',]
for folder in folders
    path = f'json_data/{folder}'
# Define the paths to your JSON files (1.json, 2.json, 3.json, 4.json)
json_files = ['1.json', '2.json', '3.json', '4.json']

# Combine the JSON files
combined_data = combine_json_files(path, json_files)

# Optionally, save the combined data back to a file or use it further
with open('combined_data.json', 'w') as outfile:
    json.dump(combined_data, outfile, indent=4)

print(f"Combined JSON data saved to 'combined_data.json'.")


In [19]:
import numpy as np
import json
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, BatchNormalization
from tensorflow.keras.regularizers import l2
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical
import os

def normalize_pose_data(pose_data, reference_x=0.5572794732116567, reference_y=0.1998999040023779):
    normalized_data = []
    outliers = {}

    for pose_index, pose in enumerate(pose_data):
        keypoints = pose['Keypoints']
        nose_point = keypoints[0]  # Assume the first keypoint is the nose

        # Offset to align the nose with reference point
        offset_x = reference_x - nose_point['X']
        offset_y = reference_y - nose_point['Y']

        pose_outliers = {'X': 0, 'Y': 0, 'dirx': 0, 'diry': 0}
        has_outliers = False

        normalized_keypoints = []
        for keypoint in keypoints:
            new_x = keypoint['X'] + offset_x
            new_y = keypoint['Y'] + offset_y

            if new_x < 0 or new_x > 1:
                pose_outliers['X'] += 1
                pose_outliers['dirx'] += new_x
                has_outliers = True
            if new_y < 0 or new_y > 1:
                pose_outliers['Y'] += 1
                pose_outliers['diry'] += new_y
                has_outliers = True

            normalized_keypoints.append({'X': new_x, 'Y': new_y})

        if not has_outliers:
            normalized_data.append({'Pose': pose['Pose'], 'Keypoints': normalized_keypoints})
        else:
            outliers[pose_index] = pose_outliers

    return normalized_data, outliers

def load_data_from_json(file_path):
    with open(file_path, 'r') as file:
        data = json.load(file)
    return data

def preprocess_data(data):
    normalized_data, outliers = normalize_pose_data(data)
    X = []
    y = []
    for entry in normalized_data:
        pose_id = entry["Pose"]
        keypoints = entry["Keypoints"]
        x_coords = [kp["X"] for kp in keypoints]
        y_coords = [kp["Y"] for kp in keypoints]
        features = x_coords + y_coords
        X.append(features)
        y.append(pose_id)
    return np.array(X), np.array(y), outliers

def create_model(input_shape, num_classes):
    model = Sequential([
        Dense(256, activation='relu', input_shape=input_shape, kernel_regularizer=l2(0.001)),
        BatchNormalization(),
        Dropout(0.2),
        Dense(128, activation='relu', kernel_regularizer=l2(0.001)),
        BatchNormalization(),
        Dropout(0.3),
        Dense(64, activation='relu', kernel_regularizer=l2(0.001)),
        BatchNormalization(),
        Dropout(0.3),
        Dense(32, activation='relu', kernel_regularizer=l2(0.001)),
        Dropout(0.4),
        Dense(num_classes, activation='softmax')
    ])
    model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    return model

def combine_data_from_json_list(json_list, club_type):
    combined_data = []
    for json_file in json_list:
        print(f'json_file {json_file}')
        json_path = f'json_data/{club_type}/{json_file}'
        if os.path.exists(json_path):
            print(f"Loading data from {json_path}")
            data = load_data_from_json(json_path)
            combined_data.extend(data)
        else:
            print(f"Warning: {json_path} not found. Skipping.")
    return combined_data

def train_and_save_model(club_type, json_list):
    print(f"Processing {club_type}...")

    # Combine data from the specified JSON files
    combined_data = combine_data_from_json_list(json_list, club_type)

    if not combined_data:
        print(f"No data available for {club_type}. Skipping.")
        return

    # Load and preprocess data
    X_data, y_data, outliers = preprocess_data(combined_data)

    print(f"Total samples: {len(combined_data)}")
    print(f"Samples after normalization: {len(X_data)}")
    print(f"Outliers removed: {len(outliers)}")

    # Encode labels
    encoder = LabelEncoder()
    y_data_encoded = encoder.fit_transform(y_data)
    num_classes = len(np.unique(y_data))
    y_data_one_hot = to_categorical(y_data_encoded, num_classes=num_classes)

    # Split data
    X_train, X_test, y_train, y_test = train_test_split(X_data, y_data_one_hot, test_size=0.2, random_state=42)

    # Create and train model
    model = create_model((34,), num_classes)
    model.fit(X_train, y_train, epochs=25, batch_size=32, validation_split=0.2, verbose=1)

    # Evaluate model
    test_loss, test_acc = model.evaluate(X_test, y_test, verbose=0)
    print(f"{club_type} - Test accuracy: {test_acc}")

    # Save model
    h5_path = f'json_data/{club_type}/pose_classification_model8.h5'
    tflite_path = f'json_data/{club_type}/pose_classification_model8.tflite'

    model.save(h5_path)

    # Convert to TFLite
    converter = tf.lite.TFLiteConverter.from_keras_model(model)
    tflite_model = converter.convert()
    with open(tflite_path, 'wb') as f:
        f.write(tflite_model)

    print(f"Model for {club_type} saved as {tflite_path}")

# Main execution
club_types = ['driver', 'fairway', 'hybrid', 'iron', 'wedge']
json_list = ['5.json','6.json','7.json','8.json']  # The JSON files you want to combine

for club_type in club_types:
    train_and_save_model(club_type, json_list)

print("Processing completed for all available club types.")


Processing driver...
json_file 5.json
Loading data from json_data/driver/5.json
json_file 6.json
Loading data from json_data/driver/6.json
json_file 7.json
Loading data from json_data/driver/7.json
json_file 8.json
Loading data from json_data/driver/8.json
Total samples: 1329
Samples after normalization: 1329
Outliers removed: 0
Epoch 1/25


/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


27/27 ━━━━━━━━━━━━━━━━━━━━ 4s 16ms/step - accuracy: 0.4017 - loss: 1.9877 - val_accuracy: 0.2676 - val_loss: 1.6802
Epoch 2/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.7213 - loss: 1.0732 - val_accuracy: 0.4930 - val_loss: 1.6109
Epoch 3/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8107 - loss: 0.8507 - val_accuracy: 0.2300 - val_loss: 1.5735
Epoch 4/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8344 - loss: 0.8098 - val_accuracy: 0.2300 - val_loss: 1.5772
Epoch 5/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8432 - loss: 0.7041 - val_accuracy: 0.3615 - val_loss: 1.4987
Epoch 6/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8279 - loss: 0.7637 - val_accuracy: 0.3427 - val_loss: 1.5412
Epoch 7/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8877 - loss: 0.6102 - val_accuracy: 0.4695 - val_loss: 1.4983
Epoch 8/25
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8979 - loss: 0.5898 - val_accuracy: 0.4883 - val_loss: 1.3627
Ep

driver - Test accuracy: 0.61654132604599
Saved artifact at '/tmp/tmphkbjnye_'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='keras_tensor_260')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  134018693806064: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693846416: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693842896: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693845008: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693842544: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693846064: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693844304: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693851168: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693850992: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018693851872: TensorSpec(shape=(), dtype=tf.r

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


...

6/6 ━━━━━━━━━━━━━━━━━━━━ 4s 70ms/step - accuracy: 0.2769 - loss: 2.5349 - val_accuracy: 0.2222 - val_loss: 1.7434
Epoch 2/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.4989 - loss: 1.7417 - val_accuracy: 0.2222 - val_loss: 1.7163
Epoch 3/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - accuracy: 0.5857 - loss: 1.3530 - val_accuracy: 0.2667 - val_loss: 1.6935
Epoch 4/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6328 - loss: 1.3557 - val_accuracy: 0.4000 - val_loss: 1.6800
Epoch 5/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6673 - loss: 1.2162 - val_accuracy: 0.4000 - val_loss: 1.6669
Epoch 6/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7496 - loss: 0.9605 - val_accuracy: 0.3556 - val_loss: 1.6560
Epoch 7/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7323 - loss: 0.9538 - val_accuracy: 0.4222 - val_loss: 1.6397
Epoch 8/25
6/6 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - accuracy: 0.7815 - loss: 0.9005 - val_accuracy: 0.5111 - val_loss: 1.6240
Epoch 9/25
6/6

iron - Test accuracy: 0.2982456088066101
Saved artifact at '/tmp/tmp0g_zyxws'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='keras_tensor_299')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  134018781480384: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781485312: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781482848: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781483552: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781480560: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781484608: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781482672: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781490064: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781489888: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781490768: TensorSpec(shape=(), dtype=tf.r

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


1/1 ━━━━━━━━━━━━━━━━━━━━ 4s 4s/step - accuracy: 0.2593 - loss: 2.5817 - val_accuracy: 0.1429 - val_loss: 1.7455
Epoch 2/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step - accuracy: 0.1481 - loss: 3.1659 - val_accuracy: 0.1429 - val_loss: 1.7415
Epoch 3/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 59ms/step - accuracy: 0.1481 - loss: 2.2988 - val_accuracy: 0.1429 - val_loss: 1.7393
Epoch 4/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step - accuracy: 0.2963 - loss: 2.5557 - val_accuracy: 0.1429 - val_loss: 1.7365
Epoch 5/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 66ms/step - accuracy: 0.3704 - loss: 1.9840 - val_accuracy: 0.1429 - val_loss: 1.7336
Epoch 6/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 160ms/step - accuracy: 0.2963 - loss: 1.8427 - val_accuracy: 0.1429 - val_loss: 1.7319
Epoch 7/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step - accuracy: 0.4815 - loss: 1.6468 - val_accuracy: 0.1429 - val_loss: 1.7294
Epoch 8/25
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 75ms/step - accuracy: 0.3333 - loss: 2.2333 - val_accuracy: 0.4286 - val_loss: 1.7263
Epoch 9/25
1

Saved artifact at '/tmp/tmpykvss7bj'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 34), dtype=tf.float32, name='keras_tensor_312')
Output Type:
  TensorSpec(shape=(None, 4), dtype=tf.float32, name=None)
Captures:
  134018781902304: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781893328: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781888576: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781899488: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781900720: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781891216: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018763420096: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018781892096: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018763086432: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018763086080: TensorSpec(shape=(), dtype=tf.resource, name=None)
  134018763443184: Te